# Playbook | Data Preparation Steps | DataFrames used

All the Snowflake tables used for this exercise has the following DataBase and Schema:

Database: **EDM_BIZOPS_PRD**
Schema: **FBI**

**Step1**: Snowflake DataSource TableName for All BNCS Data **"NK_FRACTAL_CUSTOMER_MASTER_TABLE_A2"**

Read data from this table into a spark dataframe **"cust_data"** and perform the datatype checking and transforming to correct type wherever required **(Section 1 and 2)**

**Step2**: Convert spark dataframe **"cust_data"** to **"pd_df"** and perform Missing values treatment **(Section 3a, 3b and 3c)**

**Step3**: Drop some irrelevant features from **"pd_df"** and create a new dataframe out of it **"pd_df_valid"**, perform Outlier Treatment, some additional EDA for selected features and drop features which has complete 0 values and required Univariate Analysis

Drop some additional features from **"pd_df_valid"** which are not required for modeling and generate **"pd_df_valid_bivariate"** dataframe **(Section 3d, 4 and 5)** 

Insert this data back to Snowflake table name **"FRACTAL_PLAYBOOK_DATA_A2"**


**Step4**: Read the inserted data from table **"FRACTAL_PLAYBOOK_DATA_A2"** into a dataframe **pd_df_valid_bivariate** and do a left join with Digital Experience data table **"SHX_FRACTAL_MASTER_TABLE_A2"**

Required feature engineering is done for the combined dataframe **merged_data_filtered** **(Section 6)**
			
Insert this combined data back to Snowflake table name **"NK_FRACTAL_CUSTOMER_MASTER_TABLE_L3M_S4_EDA"**

**"NK_FRACTAL_CUSTOMER_MASTER_TABLE_L3M_S4_EDA"** is used for next step of Modeling 

**Note** - All the data insertions in Snowflake tables are happening in **(Section 9)**

# 0. Essential functions for EDA

In [0]:
%pip install xgboost
%pip install shap
#%pip install nltk
%pip install pydotplus
%pip install graphviz
#%pip install python-pydot python-pydot-ng graphviz
from sklearn.tree import export_graphviz

#import nltk
#import sklearn

#print('The nltk version is {}.'.format(nltk.__version__))
#print('The scikit-learn version is {}.'.format(sklearn.__version__))

# The nltk version is 3.0.0.
# The scikit-learn version is 0.15.2.

Python interpreter will be restarted.
Collecting xgboost
 Downloading xgboost-2.0.2-py3-none-manylinux2014_x86_64.whl (297.1 MB)
Requirement already satisfied: numpy in /databricks/python3/lib/python3.8/site-packages (from xgboost) (1.20.1)
Requirement already satisfied: scipy in /databricks/python3/lib/python3.8/site-packages (from xgboost) (1.6.2)
Installing collected packages: xgboost
Successfully installed xgboost-2.0.2
Python interpreter will be restarted.
Python interpreter will be restarted.
Collecting shap
 Downloading shap-0.43.0-cp38-cp38-manylinux_2_12_x86_64.manylinux2010_x86_64.manylinux_2_17_x86_64.manylinux2014_x86_64.whl (535 kB)
Requirement already satisfied: scikit-learn in /databricks/python3/lib/python3.8/site-packages (from shap) (0.24.1)
Collecting cloudpickle
 Downloading cloudpickle-3.0.0-py3-none-any.whl (20 kB)
Collecting numba
 Downloading numba-0.58.1-cp38-cp38-manylinux2014_x86_64.manylinux_2_17_x86_64.whl (3.7 MB)
Requirement already satisfied: scipy in /databricks/python3/lib/python3.8/site-packages (from shap) (1.6.2)
Collecting packaging>20.9
 Downloading packaging-23.2-py3-none-any.whl (53 kB)
Collecting slicer==0.0.7
 Downloading slicer-0.0.7-py3-none-any.whl (14 kB)
Collecting tqdm>=4.27.0
 Downloading tqdm-4.66.1-py3-none-any.whl (78 kB)
Requirement already satisfied: pandas in /databricks/python3/lib/python3.8/site-packages (from shap) (1.2.4)
Requirement already satisfied: numpy in /databricks/python3/lib/python3.8/site-packages (from shap) (1.20.1)
Collecting importlib-metadata
 Downloading importlib_metadata-6.8.0-py3-none-any.whl (22 kB)
Collecting numpy
 Downloading numpy-1.24.4-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.3 MB)
Collecting llvmlite<0.42,>=0.41.0dev0
 Downloading llvmlite-0.41.1-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (43.6 MB)
Collecting zipp>=0.5
 Downloading zipp-3.17.0-py3-none-any.whl (7.4 kB)
Requirement already satisfied: pytz>=2017.3 in /databricks/python3/lib/python3.8/site-packages (from pandas->shap) (2020.5)
Requirement already satisfied: python-dateutil>=2.7.3 in /databricks/python3/lib/python3.8/site-packages (from pandas->shap) (2.8.1)
Requirement already satisfied: six>=1.5 in /databricks/python3/lib/python3.8/site-packages (from python-dateutil>=2.7.3->pandas->shap) (1.15.0)
Requirement already satisfied: joblib>=0.11 in /databricks/python3/lib/python3.8/site-packages (from scikit-learn->shap) (1.0.1)
Requirement already satisfied: threadpoolctl>=2.0.0 in /databricks/python3/lib/python3.8/site-packages (from scikit-learn->shap) (2.1.0)
Collecting numpy
 Downloading numpy-1.22.4-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (16.9 MB)
Installing collected packages: zipp, numpy, llvmlite, importlib-metadata, tqdm, slicer, packaging, numba, cloudpickle, shap
 Attempting uninstall: numpy
 Found existing installation: numpy 1.20.1
 Not uninstalling numpy at /databricks/python3/lib/python3.8/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-863536ba-2143-4614-8134-bf98e0f6d885
 Can't uninstall 'numpy'. No files were found to uninstall.
 Attempting uninstall: packaging
 Found existing installation: packaging 20.9
 Not uninstalling packaging at /databricks/python3/lib/python3.8/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-863536ba-2143-4614-8134-bf98e0f6d885
 Can't uninstall 'packaging'. No files were found to uninstall.
Successfully installed cloudpickle-3.0.0 importlib-metadata-6.8.0 llvmlite-0.41.1 numba-0.58.1 numpy-1.22.4 packaging-23.2 shap-0.43.0 slicer-0.0.7 tqdm-4.66.1 zipp-3.17.0
Python interpreter will be restarted.
Python interpreter will be restarted.
Collecting pydotplus
 Downloading pydotplus-2.0.2.tar.gz (278 kB)
Requirement already satisfied: pyparsing>=2.0.1 in /databricks/python3/lib/python3.8/site-packages (from pydotplus) (2.4.7)
Building wheels for collected packages: pydotplus
 Building wheel for pydotplus (setup.py): started
 Building

In [0]:
import warnings
warnings.filterwarnings("ignore")

# Import packages
from pyspark.sql.types import FloatType
from pyspark.sql.types import IntegerType
from pyspark.sql.types import StringType
from pyspark.sql.types import BooleanType
from pyspark.sql.functions import col
from pyspark.sql.functions import when
import pyspark.sql.functions as f
import warnings
warnings.filterwarnings("ignore")
#from  import *
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

### Outlier removal

In [0]:
# This function implements IQR as well as sigma threshold and find the % values that will be imputed post the outlier treatment
def percent_outliers(df_in, cols):
  df_out = pd.DataFrame(columns=['Column','IQR_LOutlier','IQR_ROutlier','Sigma_LOutlier','Sigma_ROutlier'])
  for col_name in cols:
    
    #IQR IMPLEMETATION
    q1 = df_in[col_name].quantile(0.25)
    q3 = df_in[col_name].quantile(0.75)
    iqr = q3-q1 #Interquartile range
    fence_low  = q1-1.5*iqr
    fence_high = q3+1.5*iqr
    
    l_outliers = df_in[df_in[col_name] < fence_low]
    r_outliers = df_in[df_in[col_name] > fence_high]
    l_outliers_per = (l_outliers.shape[0]/df_in.shape[0])
    r_outliers_per = (r_outliers.shape[0]/df_in.shape[0])
    
    # +/- 6SIGMA Implementation
    mean = df_in[col_name].mean()
    #np.mean(np.array(df_in[col_name]))
    std = df_in[col_name].std()
    #np.std(np.array(df_in[col_name]))
    sigma_l_out = mean - 6*std
    sigma_r_out = mean + 6*std
    
    sigma_l_outliers = df_in[df_in[col_name] < sigma_l_out]
    sigma_r_outliers = df_in[df_in[col_name] > sigma_r_out]
    sigma_l_outliers_per = (sigma_l_outliers.shape[0]/df_in.shape[0])
    sigma_r_outliers_per = (sigma_r_outliers.shape[0]/df_in.shape[0])
  
    
    df_out.loc[len(df_out)] = [col_name, l_outliers_per, r_outliers_per,sigma_l_outliers_per,sigma_r_outliers_per]
  return df_out

In [0]:
# The next function can be used when we have normal distributed values to handle upper and lower extreme values

def remove_outlier(df_in, cols, df_subset):
  for col_name in cols:
    med = df_subset[col_name].median()
    mean = df_subset[col_name].mean()
    std = df_subset[col_name].std()
    sigma_l_out = mean - 6*std
    sigma_r_out = mean + 6*std
    df_in.loc[(df_in[col_name] < sigma_l_out), col_name] =  sigma_l_out
    df_in.loc[(df_in[col_name] > sigma_r_out), col_name] =  sigma_r_out
  return df_in

In [0]:
# The next function can be used when we have to impute 0 wherever the null values are there
def impute0(df_in, cols):
  for col_name in cols:
    df_in.loc[(df_in[col_name].isnull()), col_name] =  0
  return df_in

### Aggregate function

In [0]:
# This function counts the # of customers for each feature and % of churn 
def aggregate_overall(df, categorical_cols, segment):
  overall_categorical_count = pd.DataFrame()
  
  if segment == 'Overall':
    for each_category in categorical_cols:
      x = [each_category]
      res1 = df[x].value_counts().reset_index().rename(columns={0:'Overall_Category_Count'})
      
      x.append('ECOM_CHURN_FLAG')
      res2 = df[x].value_counts().reset_index().rename(columns={0:'Ecom_Flag_Count'})

      df_out = res1.merge(res2, on=each_category, how='left')
      df_out['ECOM_CHURN_PER'] = (df_out['Ecom_Flag_Count']/(df_out['Overall_Category_Count']))
      df_out['Feature_Name'] = each_category
      df_out.rename(columns={each_category:'Feature_Values'},inplace=True)
      df_out['Filter_Metric'] = 'Overall'
      df_out['Filter_Values'] = 'Overall'
      overall_categorical_count = overall_categorical_count.append(df_out)
      
    return overall_categorical_count
    
  else:
    for each_category in categorical_cols:
        x = [each_category]
        x.append(segment)
        res1 = df[x].value_counts().reset_index().rename(columns={0:'Overall_Category_Count'})
        x.append('ECOM_CHURN_FLAG')
        res2 = df[x].value_counts().reset_index().rename(columns={0:'Ecom_Flag_Count'})
        x.remove('ECOM_CHURN_FLAG')
        df_out = res1.merge(res2, left_on=x, right_on = x,  how='left')
        df_out['ECOM_CHURN_PER'] = (df_out['Ecom_Flag_Count']/(df_out['Overall_Category_Count']))
        df_out['Feature_Name'] = each_category
        df_out.rename(columns={each_category:'Feature_Values'},inplace=True)
        df_out['Filter_Metric'] = segment
        df_out.rename(columns={segment:'Filter_Values'},inplace=True)
        df_out = df_out.astype({'Feature_Values': str})
        overall_categorical_count = overall_categorical_count.append(df_out)
        
    return overall_categorical_count

# 1. Connect & Load Data

In [0]:
#Read EDM_VIEWS_PRD DB

scope = 'SNF-DOPS-AUTAPP-AA00BZ-SCP'
snow_enc_pswd_key='SnowPRODEncPswdKey'
snow_enc_pswd_pass='SnowPRODPswdPass'
snow_user=dbutils.secrets.get(scope,'SnowPRODUsername')
snow_url='https://abs_itds_prd.west-us-2.privatelink.snowflakecomputing.com/'

from absplatform import snowflake

private_key = snowflake.Snowflake(spark, scope, snow_enc_pswd_key, snow_enc_pswd_pass).get_key()
db_options = {
            "sfURL": snow_url,
            "sfUser": snow_user,
            "pem_private_key": private_key,
            "sfDatabase": "EDM_BIZOPS_PRD",
            "sfSchema": "FBI",
            "sfWarehouse": "PROD_SUPPLY_CHAIN_WH",
            "sfRole": "ROLE_APPL_AA00BZ",
            "autopushdown": "off"
        }

In [0]:
# Read customer data (NK_FRACTAL_BNCS_CUSTOMER_MASTER) - Since we are only targeting the BNC to eom,BNC to ACI and Reactivated for this analysis
df = spark.read.format("net.snowflake.spark.snowflake").options(**db_options).option("query", "Select * FROM EDM_BIZOPS_PRD.FBI.NK_FRACTAL_CUSTOMER_MASTER_TABLE_L3M_S4" ).load()

# Shape of the dataset
print('Shape of the dataset: ', (df.count(), len(df.columns)))

# Changed for first txn
# Remove the data where store details is not present and are not mapped with the zip_cd - 1416 rows dropped
cust_data = df.filter(df.STORE_ID.isNotNull())
print(cust_data.count())

# Shape of the dataset
print('Shape of the dataset: ', (cust_data.count(), len(cust_data.columns)))

Shape of the dataset: (9114460, 262)
9079095
Shape of the dataset: (9079095, 262)

# 2. Transform to correct data type

In [0]:
# Check count of initial data types
from collections import Counter
print(Counter((x[1] for x in cust_data.dtypes)))

Counter({'double': 142, 'decimal(38,8)': 46, 'string': 30, 'decimal(18,0)': 8, 'date': 6, 'decimal(22,2)': 5, 'decimal(28,8)': 5, 'decimal(38,0)': 4, 'decimal(32,8)': 4, 'decimal(27,8)': 2, 'decimal(13,0)': 2, 'decimal(24,6)': 2, 'decimal(10,2)': 1, 'decimal(9,2)': 1, 'decimal(9,0)': 1, 'decimal(37,12)': 1, 'decimal(38,6)': 1, 'decimal(1,0)': 1})

In [0]:
# Check var types
cust_data.printSchema()

root
-- HHS_ID: string (nullable = true)
-- FRST_INSTORE_TXN_DTE: date (nullable = true)
-- LAST_INSTORE_TXN_DTE: date (nullable = true)
-- TXN_COUNT: decimal(18,0) (nullable = true)
-- TOTAL_NET_SALES: decimal(22,2) (nullable = true)
-- AOV: decimal(28,8) (nullable = true)
-- LAST_INSTORE_TXN_DTE_PRETP: date (nullable = true)
-- PRIOR_1_MONTH_STORE_TXNS: decimal(18,0) (nullable = true)
-- PRIOR_1_MONTH_TOTAL_NET_SALES: decimal(22,2) (nullable = true)
-- PRIOR_1_MONTH_STORE_AOV: decimal(28,8) (nullable = true)
-- PRIOR_1_MONTH_MKDN_AMT: decimal(27,8) (nullable = true)
-- PRIOR_3_MONTH_STORE_TXNS: decimal(18,0) (nullable = true)
-- PRIOR_3_MONTH_TOTAL_NET_SALES: decimal(22,2) (nullable = true)
-- PRIOR_3_MONTH_STORE_AOV: decimal(28,8) (nullable = true)
-- PRIOR_3_MONTH_MKDN_AMT: decimal(27,8) (nullable = true)
-- PRIOR_1MO_CLIPPED_COUPON: decimal(18,0) (nullable = true)
-- PRIOR_3MO_CLIPPED_COUPON: decimal(18,0) (nullable = true)
-- INSTORE_TXN_ID_INIT: decimal(13,0) (nullable = true)
-- INSTORE_STORE_ID_INIT: decimal(38,0) (nullable = true)
-- INSTORE_TXN_ID_LAST: decimal(13,0) (nullable = true)
-- INSTORE_STORE_ID_LAST: decimal(38,0) (nullable = true)
-- DR_CUSTOMER: decimal(38,0) (nullable = true)
-- HHID1: string (nullable = true)
-- PRIOR_1MO_ALCOHOLIC_BEVERAGES: decimal(38,8) (nullable = true)
-- PRIOR_1MO_BAKERY: decimal(38,8) (nullable = true)
-- PRIOR_1MO_BAKERY_PKD_OUTSIDE: decimal(38,8) (nullable = true)
-- PRIOR_1MO_BAR: decimal(38,8) (nullable = true)
-- PRIOR_1MO_CATERING: decimal(38,8) (nullable = true)
-- PRIOR_1MO_DAIRY: decimal(38,8) (nullable = true)
-- PRIOR_1MO_DELICATESSEN: decimal(38,8) (nullable = true)
-- PRIOR_1MO_FLORAL: decimal(38,8) (nullable = true)
-- PRIOR_1MO_FOOD_SERVICE: decimal(38,8) (nullable = true)
-- PRIOR_1MO_FRONT_END_SERVICE: decimal(38,8) (nullable = true)
-- PRIOR_1MO_FROZEN_GROCERY: decimal(38,8) (nullable = true)
-- PRIOR_1MO_FUEL_STATION: decimal(38,8) (nullable = true)
-- PRIOR_1MO_GM_HBC: decimal(38,8) (nullable = true)
-- PRIOR_1MO_GROCERY: decimal(38,8) (nullable = true)
-- PRIOR_1MO_JAMBA_JUICE: decimal(38,8) (nullable = true)
-- PRIOR_1MO_MEAT: decimal(38,8) (nullable = true)
-- PRIOR_1MO_PHARMACY: decimal(38,8) (nullable = true)
-- PRIOR_1MO_PLATED_MEAL_KITS: decimal(38,8) (nullable = true)
-- PRIOR_1MO_PRODUCE: decimal(38,8) (nullable = true)
-- PRIOR_1MO_SEAFOOD: decimal(38,8) (nullable = true)
-- PRIOR_1MO_STARBUCKS: decimal(38,8) (nullable = true)
-- PRIOR_1MO_TOBACCO: decimal(38,8) (nullable = true)
-- PRIOR_1MO_OWN_BRANDS_PERC: decimal(32,8) (nullable = true)
-- PRIOR_1MO_FRESH_SALES_PERC: decimal(32,8) (nullable = true)
-- HHID2: string (nullable = true)
-- PRIOR_3MO_ALCOHOLIC_BEVERAGES: decimal(38,8) (nullable = true)
-- PRIOR_3MO_BAKERY: decimal(38,8) (nullable = true)
-- PRIOR_3MO_BAKERY_PKD_OUTSIDE: decimal(38,8) (nullable = true)
-- PRIOR_3MO_BAR: decimal(38,8) (nullable = true)
-- PRIOR_3MO_CATERING: decimal(38,8) (nullable = true)
-- PRIOR_3MO_DAIRY: decimal(38,8) (nullable = true)
-- PRIOR_3MO_DELICATESSEN: decimal(38,8) (nullable = true)
-- PRIOR_3MO_FLORAL: decimal(38,8) (nullable = true)
-- PRIOR_3MO_FOOD_SERVICE: decimal(38,8) (nullable = true)
-- PRIOR_3MO_FRONT_END_SERVICE: decimal(38,8) (nullable = true)
-- PRIOR_3MO_FROZEN_GROCERY: decimal(38,8) (nullable = true)
-- PRIOR_3MO_FUEL_STATION: decimal(38,8) (nullable = true)
-- PRIOR_3MO_GM_HBC: decimal(38,8) (nullable = true)
-- PRIOR_3MO_GROCERY: decimal(38,8) (nullable = true)
-- PRIOR_3MO_JAMBA_JUICE: decimal(38,8) (nullable = true)
-- PRIOR_3MO_MEAT: decimal(38,8) (nullable = true)
-- PRIOR_3MO_PHARMACY: decimal(38,8) (nullable = true)
-- PRIOR_3MO_PLATED_MEAL_KITS: decimal(38,8) (nullable = true)
-- PRIOR_3MO_PRODUCE: decimal(38,8) (nullable = true)
-- PRIOR_3MO_SEAFOOD: decimal(38,8) (nullable = true)
-- PRIOR_3MO_STARBUCKS: decimal(38,8) (nullable = true)
-- PRIOR_3MO_TOBACCO: decimal(38,8) (nullable = true)
-- PRIOR_3MO_OWN_BRANDS_PERC: decimal(32,8) (nullable = true)
-- PRIOR_3MO_FRESH_SALES_PER

In [0]:
display(cust_data)

HHS_ID FRST_INSTORE_TXN_DTE LAST_INSTORE_TXN_DTE TXN_COUNT TOTAL_NET_SALES AOV LAST_INSTORE_TXN_DTE_PRETP PRIOR_1_MONTH_STORE_TXNS PRIOR_1_MONTH_TOTAL_NET_SALES PRIOR_1_MONTH_STORE_AOV PRIOR_1_MONTH_MKDN_AMT PRIOR_3_MONTH_STORE_TXNS PRIOR_3_MONTH_TOTAL_NET_SALES PRIOR_3_MONTH_STORE_AOV PRIOR_3_MONTH_MKDN_AMT PRIOR_1MO_CLIPPED_COUPON PRIOR_3MO_CLIPPED_COUPON INSTORE_TXN_ID_INIT INSTORE_STORE_ID_INIT INSTORE_TXN_ID_LAST INSTORE_STORE_ID_LAST DR_CUSTOMER HHID1 PRIOR_1MO_ALCOHOLIC_BEVERAGES PRIOR_1MO_BAKERY PRIOR_1MO_BAKERY_PKD_OUTSIDE PRIOR_1MO_BAR PRIOR_1MO_CATERING PRIOR_1MO_DAIRY PRIOR_1MO_DELICATESSEN PRIOR_1MO_FLORAL PRIOR_1MO_FOOD_SERVICE PRIOR_1MO_FRONT_END_SERVICE PRIOR_1MO_FROZEN_GROCERY PRIOR_1MO_FUEL_STATION PRIOR_1MO_GM_HBC PRIOR_1MO_GROCERY PRIOR_1MO_JAMBA_JUICE PRIOR_1MO_MEAT PRIOR_1MO_PHARMACY PRIOR_1MO_PLATED_MEAL_KITS PRIOR_1MO_PRODUCE PRIOR_1MO_SEAFOOD PRIOR_1MO_STARBUCKS PRIOR_1MO_TOBACCO PRIOR_1MO_OWN_BRANDS_PERC PRIOR_1MO_FRESH_SALES_PERC HHID2 PRIOR_3MO_ALCOHOLIC_BEVERAGES PRIOR_3MO_BAKERY PRIOR_3MO_BAKERY_PKD_OUTSIDE PRIOR_3MO_BAR PRIOR_3MO_CATERING PRIOR_3MO_DAIRY PRIOR_3MO_DELICATESSEN PRIOR_3MO_FLORAL PRIOR_3MO_FOOD_SERVICE PRIOR_3MO_FRONT_END_SERVICE PRIOR_3MO_FROZEN_GROCERY PRIOR_3MO_FUEL_STATION PRIOR_3MO_GM_HBC PRIOR_3MO_GROCERY PRIOR_3MO_JAMBA_JUICE PRIOR_3MO_MEAT PRIOR_3MO_PHARMACY PRIOR_3MO_PLATED_MEAL_KITS PRIOR_3MO_PRODUCE PRIOR_3MO_SEAFOOD PRIOR_3MO_STARBUCKS PRIOR_3MO_TOBACCO PRIOR_3MO_OWN_BRANDS_PERC PRIOR_3MO_FRESH_SALES_PERC INSTORE_TXN_DT NET_AMT MKDN_AMT TOTAL_ITEM_QTY CLIPPED_COUPONS INSTORE_FIRST_VISIT LENGTH_OF_TIME_WD_ALB_DAYS FACTS_SEGMENT_NAME TRUPRICE_SEGMENT SHOP_STYLE_SEG_SEGMENT MY_NEEDS_SEGMENT MF_FACTS_SEGMENT_NAME MF_SHOP_STYLE_SEG_SEGMENT MF_TRUPRICE_SEGMENT MF_MY_NEEDS_SEGMENT STORE_ID PERFORMANCE_DECILE ADDRESS CITY STATE IRI_SALES_SALES_DOLLAR_TY IRI_SALES_SALES_PER_CHANGE IRI_SALES_MARKET_SALES_PER_CHANGE IRI_SALES_SALES_PER_CHANGE_VS_MARKET_IN_PTS IRI_SALES_SALES_PER_SQ_FT EBIDTA_EBIDTA_DOLLAR_TY EBIDTA_EBIDTA_DOLLAR_CHANGE EBIDTA_EBIDTA_PER_CHANGE_IN_PTS EBIDTA_EBIDTA_PER_TY LABOR_LABOR_DOLLAR_TY LABOR_LABOR_PER_TY LABOR_LABOR_PER_CHANGE_IN_PTS SHRINK_SHRINK_DOLLAR_TY SHRINK_SHRINK_PER_TY SHRINK_SHRINK_PER_CHANGE_IN_PTS COMPETITION_NUMBER_OF_COMPETITORS COMPETITION_DOLLAR_AT_RISK FOOT_TRAFFIC_FOOT_TRAFFIC FOOT_TRAFFIC_FOOT_TRAFFIC_PER_CHANGE NPS_NPS_YTD NPS_NPS_YTD_FOR_ELITE_BEST NPS_NPS_LAST_4_WEEKS NPS_NPS_LAST_4_WEEKS_FOR_ELITE_BEST NPS_NPS_COUNT_YTD NPS_NPS_COUNT_YTD_FOR_ELITE_BEST NPS_NPS_COUNT_LAST_4_WEEKS NPS_NPS_COUNT_LAST_4_WEEKS_FOR_ELITE_BEST OFFERINGS_SERVICE_COUNTER_SALES_MIX_PER OFFERINGS_PHARMACY_SALES_GROWTH_PER NEW_ITEMS_PER_NEW_PRODUCTS OWN_BRANDS_OWN_BRANDS_SALES_MIX_PER ECOMM_DUG_HH_MIX_PER ECOMM_HOME_DELIVERY_MIX_PER DEPT_MIX_PRODUCE_SALES_MIX_PER DEPT_MIX_MEALS_SALES_MIX_PER DEPT_MIX_HBC_SALES_MIX_PER DEPT_MIX_ETHNIC_PRODUCTS_MIX_PER DEPT_MIX_BABY_SALES_MIX_PER DEPT_MIX_PET_SALES_MIX_PER DEPT_MIX_FUEL_SALES_MIX_PER DEPT_MIX_STARBUCKS_SALES_MIX_PER SPACE_ALLOCATION_DAIRY SPACE_ALLOCATION_FROZEN_GROCERY SPACE_ALLOCATION_GM_HBC SPACE_ALLOCATION_GROCERY SPACE_ALLOCATION_OTHERS SPACE_ALLOCATION_PKGD_BAKERY AIV_AIV_TY AIV_AIV_PER_CHANGE MARKDOWN_MARKDOWN_PER HH_COUNTS_HH_COUNT_TY HH_COUNTS_HH_COUNT_PER_CHANGE SNAP_PER_OF_SALES_FROM_SNAP OTHER_PER_HH_REDEEMING_J4U_OFFERS FACTS_ELITEBEST_PER_OF_SALES FACTS_GOOD_PER_OF_SALES FACTS_OCCASIONAL_PER_OF_SALES TRUPRICE_MOST_PRICE_DRIVEN_PER_OF_SALES TRUPRICE_PRICE_DRIVEN_PER_OF_SALES TRUPRICE_PRICE_NEUTRAL_PER_OF_SALES TRUPRICE_QUALITY_DRIVEN_PER_OF_SALES TRUPRICE_MOST_QUALITY_DRIVEN_PER_OF_SALES SHOPSTYLES_ORGANIC_LIVING_PER_OF_SALES SHOPSTYLES_COOKING_FROM_SCRATCH_PER_OF_SALES SHOPSTYLES_CONVENIENCE_SEEKERS_PER_OF_SALES SHOPSTYLES_HEALTHIER_ALTERNATIVES_PER_OF_SALES SHOPSTYLES_FAMILY_FOCUSED_PER_OF_SALES SHOPSTYLES_CONVENIENTLY_FRESH_PER_OF_SALES MYNEEDS_EASY_EATING_PER_OF_SALES MYNEEDS_ONE_STOP_LOW_PRICE_PER_OF_SALES MYNEEDS_HEALTHY_FOODIES_PER_OF_SALES MYNEEDS_CHASING_PRICE_PER_OF_SALES MYNEEDS_SCRATCH_FOODI

In [0]:
# Changed for first txn
last_txn_cols = (
'HHID1',
'HHID2',
'INSTORE_FIRST_VISIT',
'FACTS_SEGMENT_NAME',
'TRUPRICE_SEGMENT',
'SHOP_STYLE_SEG_SEGMENT',
'MY_NEEDS_SEGMENT'
)

cust_data = cust_data.drop(*last_txn_cols)
#cust_data.printSchema()
print('Shape of the dataset: ', (cust_data.count(), len(cust_data.columns)))

Shape of the dataset: (9079095, 255)

In [0]:
cust_data = cust_data.withColumn('DR_CUSTOMER', when (cust_data.DR_CUSTOMER.isNotNull(), 1).otherwise(0))
cust_data.select('DR_CUSTOMER').distinct().collect()

# STARBUCKS has 2 values (Y and N), so converting them to 1 and 0
cust_data = cust_data.withColumn('STARBUCKS', when (cust_data.STARBUCKS == 'N', 0).otherwise(1))
cust_data.select('STARBUCKS').distinct().collect()

# INSTACART has 2 values (Y and N), so converting them to 1 and 0
cust_data = cust_data.withColumn('INSTACART', when (cust_data.INSTACART == 'N', 0).otherwise(1))
cust_data.select('INSTACART').distinct().collect()

# FUEL has 2 values (Y and N), so converting them to 1 and 0
cust_data = cust_data.withColumn('FUEL', when (cust_data.FUEL == 'N', 0).otherwise(1))
cust_data.select('FUEL').distinct().collect()

# PHARMACY has 2 values (Y and N), so converting them to 1 and 0
cust_data = cust_data.withColumn('PHARMACY', when (cust_data.PHARMACY == 'N', 0).otherwise(1))
cust_data.select('PHARMACY').distinct().collect()

# MFC has 3 values (True, False and None), so converting them to 1, 0 and None
cust_data = cust_data.withColumn('MFC', when (cust_data.MFC == False, 0).when (cust_data.MFC == True, 1))
cust_data.select('MFC').distinct().collect()

Out[11]: [Row(MFC=None)]

## 2.a Convert _AMT vars to float type

In [0]:
# Select columns to keep as float
amtcols = cust_data.select(cust_data.colRegex("`.+_AMT$`")).columns

# look at type of AMT columns
print(len(amtcols),'_AMT Columns overview')
pd.DataFrame(cust_data.select(*amtcols).dtypes, columns = ['Column Name','Data type'])

4 _AMT Columns overview
Out[12]:

Column Name 
 Data type 
 
 
 
 
 0 
 PRIOR_1_MONTH_MKDN_AMT 
 decimal(27,8) 
 
 
 1 
 PRIOR_3_MONTH_MKDN_AMT 
 decimal(27,8) 
 
 
 2 
 NET_AMT 
 decimal(10,2) 
 
 
 3 
 MKDN_AMT 
 decimal(9,2)

In [0]:
#convert AMT columns to floats
for col in amtcols:
    cust_data = cust_data.withColumn(col, cust_data[col].cast(FloatType()))
    
# look at new FLOAT type of previous AMT decimal columns
print(len(amtcols),'Float Columns overview')
pd.DataFrame(cust_data.select(*amtcols).dtypes, columns = ['Column Name','Data type'])  

4 Float Columns overview
Out[13]:

Column Name 
 Data type 
 
 
 
 
 0 
 PRIOR_1_MONTH_MKDN_AMT 
 float 
 
 
 1 
 PRIOR_3_MONTH_MKDN_AMT 
 float 
 
 
 2 
 NET_AMT 
 float 
 
 
 3 
 MKDN_AMT 
 float

## 2.b Convert _ID columns to strings

In [0]:
# Select columns to keep as float
IDcols= cust_data.select(cust_data.colRegex("`.+_ID$`")).columns

# Select other string columns
IDcols = IDcols + ['MF_FACTS_SEGMENT_NAME', 'MF_SHOP_STYLE_SEG_SEGMENT', 'MF_TRUPRICE_SEGMENT', 'MF_MY_NEEDS_SEGMENT', 'LU_BANNER', 'LU_DIVISION', 'LU_DISTRICT', 'MSA', 'CLUSTER', 'URBANICITY', 'BANNER','DIVISION','DISTRICT']

# look at new FLOAT type of previous decimal columns
print(len(IDcols),'IDcols Columns overview')
pd.DataFrame(cust_data.select(*IDcols).dtypes, columns = ['Column Name','Data type'])

15 IDcols Columns overview
Out[14]:

Column Name 
 Data type 
 
 
 
 
 0 
 HHS_ID 
 string 
 
 
 1 
 STORE_ID 
 double 
 
 
 2 
 MF_FACTS_SEGMENT_NAME 
 string 
 
 
 3 
 MF_SHOP_STYLE_SEG_SEGMENT 
 string 
 
 
 4 
 MF_TRUPRICE_SEGMENT 
 string 
 
 
 5 
 MF_MY_NEEDS_SEGMENT 
 string 
 
 
 6 
 LU_BANNER 
 string 
 
 
 7 
 LU_DIVISION 
 string 
 
 
 8 
 LU_DISTRICT 
 string 
 
 
 9 
 MSA 
 string 
 
 
 10 
 CLUSTER 
 string 
 
 
 11 
 URBANICITY 
 string 
 
 
 12 
 BANNER 
 string 
 
 
 13 
 DIVISION 
 string 
 
 
 14 
 DISTRICT 
 string

In [0]:
#convert _ID columns to strings
for col in IDcols:
    cust_data = cust_data.withColumn(col, cust_data[col].cast(StringType()))
    
# look at new FLOAT type of previous AMT decimal columns
print(len(IDcols),'_ID Columns overview')
pd.DataFrame(cust_data.select(*IDcols).dtypes, columns = ['Column Name','Data type'])  

15 _ID Columns overview
Out[15]:

Column Name 
 Data type 
 
 
 
 
 0 
 HHS_ID 
 string 
 
 
 1 
 STORE_ID 
 string 
 
 
 2 
 MF_FACTS_SEGMENT_NAME 
 string 
 
 
 3 
 MF_SHOP_STYLE_SEG_SEGMENT 
 string 
 
 
 4 
 MF_TRUPRICE_SEGMENT 
 string 
 
 
 5 
 MF_MY_NEEDS_SEGMENT 
 string 
 
 
 6 
 LU_BANNER 
 string 
 
 
 7 
 LU_DIVISION 
 string 
 
 
 8 
 LU_DISTRICT 
 string 
 
 
 9 
 MSA 
 string 
 
 
 10 
 CLUSTER 
 string 
 
 
 11 
 URBANICITY 
 string 
 
 
 12 
 BANNER 
 string 
 
 
 13 
 DIVISION 
 string 
 
 
 14 
 DISTRICT 
 string

## 2.c Convert _FLAG columns to boolean 

In [0]:

# Select columns to keep as bool
FLAGcols= list(set(cust_data.select(cust_data.colRegex("`.+_FLAG$`")).columns)) + ['STARBUCKS', 'INSTACART','FUEL','PHARMACY','MFC']
# look at FLAG columns
print( len(FLAGcols), '_FLAG Columns overview')

pd.DataFrame(cust_data.select(*FLAGcols).dtypes, columns = ['Column Name','Data type']) 

6 _FLAG Columns overview
Out[16]:

Column Name 
 Data type 
 
 
 
 
 0 
 EMP_FLAG 
 decimal(1,0) 
 
 
 1 
 STARBUCKS 
 int 
 
 
 2 
 INSTACART 
 int 
 
 
 3 
 FUEL 
 int 
 
 
 4 
 PHARMACY 
 int 
 
 
 5 
 MFC 
 int

In [0]:
#convert _FLAG columns to BOOL
for col in FLAGcols:
    cust_data = cust_data.withColumn(col, cust_data[col].cast(BooleanType()))
    
# look at new BOOL type of previous FLAG decimal columns
print( len(FLAGcols),'_FLAG Columns overview')
pd.DataFrame(cust_data.select(FLAGcols).dtypes, columns = ['Column Name','Data type'])  

6 _FLAG Columns overview
Out[17]:

Column Name 
 Data type 
 
 
 
 
 0 
 EMP_FLAG 
 boolean 
 
 
 1 
 STARBUCKS 
 boolean 
 
 
 2 
 INSTACART 
 boolean 
 
 
 3 
 FUEL 
 boolean 
 
 
 4 
 PHARMACY 
 boolean 
 
 
 5 
 MFC 
 boolean

## 2.d Convert decimal and double cols to float

In [0]:
#Find all decimal columns in SparkDF
decimals_cols = [c for c in cust_data.columns if 'Decimal' in str(cust_data.schema[c].dataType)]

#Look at decimal columns
print(len(decimals_cols),' Decimal Columns Overview')
pd.DataFrame(cust_data.select(*decimals_cols).dtypes, columns = ['Column Name','Data type'])

78 Decimal Columns Overview
Out[18]:

Column Name 
 Data type 
 
 
 
 
 0 
 TXN_COUNT 
 decimal(18,0) 
 
 
 1 
 TOTAL_NET_SALES 
 decimal(22,2) 
 
 
 2 
 AOV 
 decimal(28,8) 
 
 
 3 
 PRIOR_1_MONTH_STORE_TXNS 
 decimal(18,0) 
 
 
 4 
 PRIOR_1_MONTH_TOTAL_NET_SALES 
 decimal(22,2) 
 
 
 ... 
 ... 
 ... 
 
 
 73 
 ECOM_TXNCOUNTPERWEEK 
 decimal(24,6) 
 
 
 74 
 INSTORE_SALES 
 decimal(22,2) 
 
 
 75 
 INSTORE_TXN_COUNT 
 decimal(18,0) 
 
 
 76 
 INSTORE_AOV 
 decimal(28,8) 
 
 
 77 
 INSTORE_TXNCOUNTPERWEEK 
 decimal(24,6) 
 
 
 
 78 rows × 2 columns

In [0]:
#convert decimals columns to float
for col in decimals_cols:
    cust_data = cust_data.withColumn(col, cust_data[col].cast(FloatType()))
    
# look at new float type of previous decimal columns
print(len(decimals_cols),' Float Columns overview')
pd.DataFrame(cust_data.select(*decimals_cols).dtypes, columns = ['Column Name','Data type'])  

78 Float Columns overview
Out[19]:

Column Name 
 Data type 
 
 
 
 
 0 
 TXN_COUNT 
 float 
 
 
 1 
 TOTAL_NET_SALES 
 float 
 
 
 2 
 AOV 
 float 
 
 
 3 
 PRIOR_1_MONTH_STORE_TXNS 
 float 
 
 
 4 
 PRIOR_1_MONTH_TOTAL_NET_SALES 
 float 
 
 
 ... 
 ... 
 ... 
 
 
 73 
 ECOM_TXNCOUNTPERWEEK 
 float 
 
 
 74 
 INSTORE_SALES 
 float 
 
 
 75 
 INSTORE_TXN_COUNT 
 float 
 
 
 76 
 INSTORE_AOV 
 float 
 
 
 77 
 INSTORE_TXNCOUNTPERWEEK 
 float 
 
 
 
 78 rows × 2 columns

In [0]:
#Find all double columns in SparkDF
double_cols = [c for c in cust_data.columns if 'Double' in str(cust_data.schema[c].dataType)]

#Look at double columns
print(len(double_cols),' Double Columns Overview')
pd.DataFrame(cust_data.select(*double_cols).dtypes, columns = ['Column Name','Data type'])

141 Double Columns Overview
Out[20]:

Column Name 
 Data type 
 
 
 
 
 0 
 PERFORMANCE_DECILE 
 double 
 
 
 1 
 IRI_SALES_SALES_DOLLAR_TY 
 double 
 
 
 2 
 IRI_SALES_SALES_PER_CHANGE 
 double 
 
 
 3 
 IRI_SALES_MARKET_SALES_PER_CHANGE 
 double 
 
 
 4 
 IRI_SALES_SALES_PER_CHANGE_VS_MARKET_IN_PTS 
 double 
 
 
 ... 
 ... 
 ... 
 
 
 136 
 ETHNICITY_OTHE_TRADE_AREAR_PER 
 double 
 
 
 137 
 ETHNICITY_OTHER_VARIANCE_IN_PTS 
 double 
 
 
 138 
 LAST_REMODEL_AMOUNT 
 double 
 
 
 139 
 BUILDING_SIZE_SQ_FT 
 double 
 
 
 140 
 SELLING_AREA_SQ_FT 
 double 
 
 
 
 141 rows × 2 columns

In [0]:
#convert double columns to float
for col in double_cols:
    cust_data = cust_data.withColumn(col, cust_data[col].cast(FloatType()))
    
# look at new float type of previous double columns
print(len(double_cols),' Float Columns overview')
pd.DataFrame(cust_data.select(*double_cols).dtypes, columns = ['Column Name','Data type'])  

141 Float Columns overview
Out[21]:

Column Name 
 Data type 
 
 
 
 
 0 
 PERFORMANCE_DECILE 
 float 
 
 
 1 
 IRI_SALES_SALES_DOLLAR_TY 
 float 
 
 
 2 
 IRI_SALES_SALES_PER_CHANGE 
 float 
 
 
 3 
 IRI_SALES_MARKET_SALES_PER_CHANGE 
 float 
 
 
 4 
 IRI_SALES_SALES_PER_CHANGE_VS_MARKET_IN_PTS 
 float 
 
 
 ... 
 ... 
 ... 
 
 
 136 
 ETHNICITY_OTHE_TRADE_AREAR_PER 
 float 
 
 
 137 
 ETHNICITY_OTHER_VARIANCE_IN_PTS 
 float 
 
 
 138 
 LAST_REMODEL_AMOUNT 
 float 
 
 
 139 
 BUILDING_SIZE_SQ_FT 
 float 
 
 
 140 
 SELLING_AREA_SQ_FT 
 float 
 
 
 
 141 rows × 2 columns

## 2.e Count columns by final data type and Display

In [0]:
# Count columns by data type
print(Counter((x[1] for x in cust_data.dtypes)))
print('Shape of the dataset: ', (cust_data.count(), len(cust_data.columns)))

Counter({'float': 223, 'string': 20, 'boolean': 6, 'date': 5, 'int': 1})
Shape of the dataset: (9079095, 255)

## 2.f Convert Spark object to Pandas Dataframe

In [0]:
# Show final data as Pandas dataset 
pd_df = cust_data.toPandas()
pd_df.head()

Out[23]:

HHS_ID 
 FRST_INSTORE_TXN_DTE 
 LAST_INSTORE_TXN_DTE 
 TXN_COUNT 
 TOTAL_NET_SALES 
 AOV 
 LAST_INSTORE_TXN_DTE_PRETP 
 PRIOR_1_MONTH_STORE_TXNS 
 PRIOR_1_MONTH_TOTAL_NET_SALES 
 PRIOR_1_MONTH_STORE_AOV 
 PRIOR_1_MONTH_MKDN_AMT 
 PRIOR_3_MONTH_STORE_TXNS 
 PRIOR_3_MONTH_TOTAL_NET_SALES 
 PRIOR_3_MONTH_STORE_AOV 
 PRIOR_3_MONTH_MKDN_AMT 
 PRIOR_1MO_CLIPPED_COUPON 
 PRIOR_3MO_CLIPPED_COUPON 
 INSTORE_TXN_ID_INIT 
 INSTORE_STORE_ID_INIT 
 INSTORE_TXN_ID_LAST 
 INSTORE_STORE_ID_LAST 
 DR_CUSTOMER 
 PRIOR_1MO_ALCOHOLIC_BEVERAGES 
 PRIOR_1MO_BAKERY 
 PRIOR_1MO_BAKERY_PKD_OUTSIDE 
 PRIOR_1MO_BAR 
 PRIOR_1MO_CATERING 
 PRIOR_1MO_DAIRY 
 PRIOR_1MO_DELICATESSEN 
 PRIOR_1MO_FLORAL 
 PRIOR_1MO_FOOD_SERVICE 
 PRIOR_1MO_FRONT_END_SERVICE 
 PRIOR_1MO_FROZEN_GROCERY 
 PRIOR_1MO_FUEL_STATION 
 PRIOR_1MO_GM_HBC 
 PRIOR_1MO_GROCERY 
 PRIOR_1MO_JAMBA_JUICE 
 PRIOR_1MO_MEAT 
 PRIOR_1MO_PHARMACY 
 PRIOR_1MO_PLATED_MEAL_KITS 
 ... 
 ETHNICITY_ASIAN_VARIANCE_IN_PTS 
 ETHNICITY_HISPANIC_STORE_PER 
 ETHNICITY_HISPANIC_TRADE_AREA_PER 
 ETHNICITY_HISPANIC_VARIANCE_IN_PTS 
 ETHNICITY_OTHER_STORE_PER 
 ETHNICITY_OTHE_TRADE_AREAR_PER 
 ETHNICITY_OTHER_VARIANCE_IN_PTS 
 BANNER 
 DIVISION 
 DISTRICT 
 MSA 
 CLUSTER 
 URBANICITY 
 STARBUCKS 
 INSTACART 
 FUEL 
 PHARMACY 
 DUG 
 HOME_DELIVERY 
 MFC 
 LAST_REMODEL_DATE 
 LAST_REMODEL_AMOUNT 
 BUILDING_SIZE_SQ_FT 
 SELLING_AREA_SQ_FT 
 LU_BANNER 
 LU_DIVISION 
 LU_DISTRICT 
 AVG_SOOS 
 I_SALES_PER 
 U_SALES_PER 
 D_SALES_PER 
 ECOM_SALES 
 ECOM_TXN_COUNT 
 ECOM_AOV 
 ECOM_TXNCOUNTPERWEEK 
 INSTORE_SALES 
 INSTORE_TXN_COUNT 
 INSTORE_AOV 
 INSTORE_TXNCOUNTPERWEEK 
 EMP_FLAG 
 
 
 
 
 0 
 250013853375 
 2023-09-01 
 2023-11-08 
 9.0 
 179.940002 
 19.993334 
 2023-08-10 
 3.0 
 44.169998 
 14.723333 
 -0.990000 
 9.0 
 142.279999 
 15.808888 
 -0.882222 
 0.0 
 0.0 
 5.771579e+09 
 970.0 
 6.187555e+09 
 970.0 
 1 
 NaN 
 12.076318 
 NaN 
 NaN 
 NaN 
 11.200897 
 20.179573 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 NaN 
 11.290684 
 NaN 
 6.711560 
 NaN 
 NaN 
 ... 
 -12.0 
 0.17 
 0.16 
 1.0 
 0.06 
 0.05 
 1.0 
 SAFEWAY 
 NOR. CALIFORNIA 
 PENNINSULA 
 SAN FRAN-OAK-BERK CA 
 Medium Premium 
 Urban 
 True 
 True 
 False 
 True 
 Y 
 Y 
 None 
 1970-01-01 
 2805000.0 
 41740.0 
 30002.0 
 SAFEWAY 
 NOR. CALIFORNIA 
 PENNINSULA 
 0.013575 
 0.647854 
 0.052968 
 0.299177 
 116713.679688 
 1367.0 
 85.379433 
 105.153847 
 11236189.0 
 318114.0 
 35.321266 
 24470.308594 
 False 
 
 
 1 
 990056121312 
 2023-08-23 
 2023-11-10 
 6.0 
 837.859985 
 139.643326 
 2023-08-04 
 1.0 
 316.339996 
 316.339996 
 -27.420000 
 5.0 
 793.159973 
 158.632004 
 -19.573999 
 0.0 
 0.0 
 5.714301e+09 
 3735.0 
 6.195261e+09 
 3798.0 
 1 
 NaN 
 1.825971 
 1.199028 
 NaN 
 NaN 
 5.044277 
 7.666988 
 NaN 
 NaN 
 13.061309 
 8.325278 
 NaN 
 7.959562 
 45.280949 
 NaN 
 8.738016 
 NaN 
 NaN 
 ... 
 -5.0 
 0.03 
 0.03 
 0.0 
 0.05 
 0.03 
 2.0 
 ACME 
 MID-ATLANTIC 
 MAIN LINE SUBUR 
 PH-CMD-WM PA-NJ-DE-MD 
 High Mainstream 
 Suburban 
 False 
 True 
 False 
 True 
 Y 
 Y 
 None 
 1970-01-01 
 1195000.0 
 53357.0 
 0.0 
 ACME 
 MID-ATLANTIC 
 MAIN LINE SUBUR 
 0.068910 
 0.783542 
 0.051212 
 0.165246 
 82939.031250 
 781.0 
 106.195938 
 60.076923 
 6558639.0 
 175464.0 
 37.378830 
 13497.230469 
 False 
 
 
 2 
 990031543568 
 2023-08-17 
 2023-11-11 
 16.0 
 428.320007 
 26.770000 
 2023-08-06 
 4.0 
 103.300003 
 25.825001 
 -4.387500 
 15.0 
 417.329987 
 27.822001 
 -7.337333 
 0.0 
 2.0 
 5.676692e+09 
 2428.0 
 6.202629e+09 
 2428.0 
 1 
 NaN 
 NaN 
 3.136119 
 NaN 
 NaN 
 13.380223 
 16.541166 
 NaN 
 5.370293 
 NaN 
 NaN 
 NaN 
 NaN 
 61.572197 
 NaN 
 NaN 
 NaN 
 NaN 
 ... 
 -1.0 
 0.10 
 0.12 
 -2.0 
 0.05 
 0.03 
 2.0 
 ACME 
 MID-ATLANTIC 
 NY/CT 
 PGPSIE-NBRGH-MDLTN NY 
 High Mainstream 
 Rural 
 False 
 True 
 False 
 True 
 Y 
 Y 
 None 
 1970-01-01 
 1498000.0 
 47469.0 
 0.0 
 ACME 
 MID-ATLANTIC 
 NY/CT 
 0.000000 
 0.651737 
 0.092199 
 0.256063 
 199837.593750 
 1853.0 
 107.845436 
 142.538467 
 6568394.5 
 151004.0 
 43.

In [0]:
# Data types in pandas
pd_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9079095 entries, 0 to 9079094
Columns: 255 entries, HHS_ID to EMP_FLAG
dtypes: bool(5), float32(223), int32(1), object(26)
memory usage: 9.4+ GB

In [0]:
#Check duplicated values
pd_df[pd_df.duplicated()].count().sort_values(ascending=False)

Out[25]: HHS_ID 0
AGE_65_74_TRADE_AREA_PER 0
AGE_25_34_STORE_PER 0
AGE_25_34_TRADE_AREA_PER 0
AGE_25_34_VARIANCE_IN_PTS 0
 ..
EBIDTA_EBIDTA_DOLLAR_TY 0
EBIDTA_EBIDTA_DOLLAR_CHANGE 0
EBIDTA_EBIDTA_PER_CHANGE_IN_PTS 0
EBIDTA_EBIDTA_PER_TY 0
EMP_FLAG 0
Length: 255, dtype: int64

In [0]:
# Create a copy of data before moving forward
#pd_df_copy = pd_df.copy()
#pd_df = pd_df_copy.copy()

# 3. Clean dataset

## 3.a. Missing & outlier values

### Group features by data type

In [0]:
# Count columns by data type
print('Shape of the dataset: ', pd_df.shape)

# fcols, string_columns, dtcols, bcols, 

bcols = pd_df.select_dtypes('bool').columns.to_list()
print('Boolean columns: ',len(bcols))

dtcols = pd_df.select_dtypes('datetime').columns.to_list()
print('Datetime columns: ',len(dtcols))

f32cols = pd_df.select_dtypes('float32').columns.to_list()
f64cols = pd_df.select_dtypes('float64').columns.to_list()
intcols = pd_df.select_dtypes('int32').columns.to_list()
ficols = f32cols + f64cols + intcols
print('Float columns: ',len(ficols))

string_columns = pd_df.select_dtypes('object').columns.to_list()
print('String columns: ',len(string_columns))

Shape of the dataset: (9079095, 255)
Boolean columns: 5
Datetime columns: 0
Float columns: 224
String columns: 26

In [0]:
# Check whether all the metrics are covered in these 4 buckets or are we missing something 
all_columns_expected = pd_df.columns.to_list()
all_columns_actual = bcols + dtcols + ficols + string_columns
for x in all_columns_expected:
  if x not in all_columns_actual:
    print(x)

### Check % missing values for each variable set

In [0]:
# Missing values in string cols
a = ((pd_df.isna().sum()/len(pd_df)).sort_values(ascending= False)).reset_index()
missing_values = pd.DataFrame(pd.concat([a]))
display(missing_values)

index 0 MFC 1.0 PRIOR_3MO_PLATED_MEAL_KITS 1.0 PRIOR_3MO_JAMBA_JUICE 1.0 EBIDTA_EBIDTA_PER_TY 1.0 PRIOR_1MO_PLATED_MEAL_KITS 1.0 PRIOR_1MO_JAMBA_JUICE 1.0 EBIDTA_EBIDTA_PER_CHANGE_IN_PTS 1.0 EBIDTA_EBIDTA_DOLLAR_CHANGE 1.0 EBIDTA_EBIDTA_DOLLAR_TY 1.0 PRIOR_1MO_CATERING 1.0 PRIOR_3MO_CATERING 0.9999996405705296 PRIOR_1MO_BAR 0.9999935302695325 PRIOR_3MO_BAR 0.999989576545358 PRIOR_1MO_FUEL_STATION 0.9922607646430668 PRIOR_3MO_FUEL_STATION 0.9825673112554979 PRIOR_1MO_TOBACCO 0.9728526515291747 PRIOR_3MO_TOBACCO 0.9523694848692773 PRIOR_1MO_FRONT_END_SERVICE 0.9472105936804391 PRIOR_1MO_STARBUCKS 0.906834802980533 PRIOR_3MO_FRONT_END_SERVICE 0.8792424808253363 PRIOR_1MO_PHARMACY 0.8646180145331712 PRIOR_3MO_STARBUCKS 0.8283228266108641 PRIOR_1MO_FLORAL 0.8112718519639406 PRIOR_3MO_PHARMACY 0.8047431750633585 PRIOR_1MO_SEAFOOD 0.7314048264908146 PRIOR_3MO_FLORAL 0.6266462319031755 PRIOR_1MO_ALCOHOLIC_BEVERAGES 0.5965353874487948 PRIOR_3MO_SEAFOOD 0.5284033747551836 PRIOR_1MO_FOOD_SERVICE 0.4938913164355955 PRIOR_3MO_ALCOHOLIC_BEVERAGES 0.42588546348609924 PRIOR_1MO_DELICATESSEN 0.3895992613005524 PRIOR_1MO_BAKERY 0.35162158402724186 PRIOR_1MO_BAKERY_PKD_OUTSIDE 0.3156904981584631 PRIOR_3MO_FOOD_SERVICE 0.2786441026429927 PRIOR_1MO_FROZEN_GROCERY 0.21993920609937434 OFFERINGS_PHARMACY_SALES_GROWTH_PER 0.20454376359317328 PRIOR_1MO_GM_HBC 0.17577466935184444 PRIOR_1MO_MEAT 0.1665197199181795 PRIOR_3MO_DELICATESSEN 0.16588317032607802 PRIOR_3MO_BAKERY 0.15013980009251715 PRIOR_3MO_BAKERY_PKD_OUTSIDE 0.11712224951090634 MSA 0.11503683972356998 LAST_REMODEL_DATE 0.08382829766654794 LAST_REMODEL_AMOUNT 0.08382829766654794 PRIOR_1MO_DAIRY 0.06328474685562113 PRIOR_1MO_PRODUCE 0.058471986246790744 PRIOR_3MO_FROZEN_GROCERY 0.057082791343644405 PRIOR_3MO_MEAT 0.04844390402226737 PRIOR_3MO_GM_HBC 0.045976420707881965 AVG_SOOS 0.02764192342211361 ECOM_SALES 0.0271282987088934 ECOM_TXN_COUNT 0.0271282987088934 ECOM_AOV 0.0271282987088934 ECOM_TXNCOUNTPERWEEK 0.0271282987088934 PRIOR_1MO_OWN_BRANDS_PERC 0.01711207765689366 PRIOR_1MO_GROCERY 0.015573360094055504 PRIOR_1MO_FRESH_SALES_PERC 0.01483832682706087 NPS_NPS_LAST_4_WEEKS_FOR_ELITE_BEST 0.011102416911587898 PRIOR_3MO_DAIRY 0.009510503787128616 PRIOR_3MO_PRODUCE 0.00902024198948525 PRIOR_1_MONTH_STORE_AOV 0.007391667059043839 PRIOR_1_MONTH_MKDN_AMT 0.007391667059043839 PRIOR_1_MONTH_TOTAL_NET_SALES 0.007391667059043839 LAST_INSTORE_TXN_DTE_PRETP 0.005575829374517241 CLUSTER 0.0023855333951312402 MF_MY_NEEDS_SEGMENT 0.001393148627320881 PRIOR_3MO_OWN_BRANDS_PERC 0.0011153096466916135 PRIOR_3MO_FRESH_SALES_PERC 0.0010279682853812486 PRIOR_3MO_GROCERY 9.503315197720354E-4 IRI_SALES_SALES_PER_SQ_FT 7.569584646898286E-4 PRIOR_3_MONTH_TOTAL_NET_SALES 1.736044342094906E-4 PRIOR_3_MONTH_STORE_AOV 1.736044342094906E-4 PRIOR_3_MONTH_MKDN_AMT 1.736044342094906E-4 MF_FACTS_SEGMENT_NAME 1.3550491034571005E-4 MF_SHOP_STYLE_SEG_SEGMENT 1.3550491034571005E-4 MF_TRUPRICE_SEGMENT 1.3550491034571005E-4 NPS_NPS_YTD_FOR_ELITE_BEST 1.275974619966235E-4 INCOME_150K_200K_VARIANCE_IN_PTS 0.0 INCOME_25K_35K_TRADE_AREA_PER 0.0 INCOME_25K_35K_VARIANCE_IN_PTS 0.0 INCOME_40K_50K_STORE_PER 0.0 INCOME_35K_50K_TRADE_AREA_PER 0.0 INCOME_35K_50K_VARIANCE_IN_PTS 0.0 INCOME_50K_75K_STORE_PER 0.0 AGE_25_34_VARIANCE_IN_PTS 0.0 INCOME_50K_75K_TRADE_AREA_PER 0.0 INCOME_10K_25K_VARIANCE_IN_PTS 0.0 INCOME_50K_75K_VARIANCE_IN_PTS 0.0 INCOME_75K_100K_STORE_PER 0.0 INCOME_75K_100K_TRADE_AREA_PER 0.0 INCOME_75K_100K_VARIANCE_IN_PTS 0.0 INCOME_100K_150K_STORE_PER 0.0 AGE_25_34_TRADE_AREA_PER 0.0 INCOME_100K_150K_TRADE_AREA_PER 0.0 INCOME_100K_150K_VARIANCE_IN_PTS 0.0 INCOME_150K_200K_STORE_PER 0.0 INCOME_30K_40K_STORE_PER 0.0 AGE_35_44_TRADE_AREA_PER 0.0 INCOME_10K_25K_TRADE_AREA_PER 0.0 INCOME_10K_25K_STORE_PER 0.0 AGE_55_64_TRADE_AREA_PER 0.0 AGE_55_64_VARIANCE_IN_PTS 0.0 AGE_65_74_STORE_PER 0.0 AGE_45_54_VARIANCE_IN_PTS 0.0 AGE_45_54_TRADE_AREA_PER 0.0 AGE_45_54_STORE_PER 0.0 AGE_65_74_TRADE_AREA_PER 0.0 AGE_65_74_VARIANCE_IN_PTS 0.

### Handling the missing values of Prior Instore transactions metrics

In [0]:
prior_txns_metrics = [
  'PRIOR_1_MONTH_STORE_TXNS',
  'PRIOR_1_MONTH_TOTAL_NET_SALES',
  'PRIOR_1_MONTH_STORE_AOV',
  'PRIOR_1_MONTH_MKDN_AMT',
  'PRIOR_3_MONTH_STORE_TXNS',
  'PRIOR_3_MONTH_TOTAL_NET_SALES',
  'PRIOR_3_MONTH_STORE_AOV',
  'PRIOR_3_MONTH_MKDN_AMT',
  'PRIOR_1MO_CLIPPED_COUPON',
  'PRIOR_3MO_CLIPPED_COUPON'
]

((pd_df[prior_txns_metrics].isna().sum()/len(pd_df)).sort_values(ascending= False))

Out[28]: PRIOR_1_MONTH_TOTAL_NET_SALES 0.126407
PRIOR_1_MONTH_STORE_AOV 0.126407
PRIOR_1_MONTH_MKDN_AMT 0.126407
PRIOR_3_MONTH_TOTAL_NET_SALES 0.007019
PRIOR_3_MONTH_STORE_AOV 0.007019
PRIOR_3_MONTH_MKDN_AMT 0.007019
PRIOR_1_MONTH_STORE_TXNS 0.000000
PRIOR_3_MONTH_STORE_TXNS 0.000000
PRIOR_1MO_CLIPPED_COUPON 0.000000
PRIOR_3MO_CLIPPED_COUPON 0.000000
dtype: float64

In [0]:
# wherever the #instore txns is 0, the other metrics will be 0 for sure

pd_df.loc[(pd_df['PRIOR_3_MONTH_STORE_TXNS'] == 0),'PRIOR_3_MONTH_TOTAL_NET_SALES'] = 0
pd_df.loc[(pd_df['PRIOR_3_MONTH_STORE_TXNS'] == 0),'PRIOR_3_MONTH_STORE_AOV'] = 0
pd_df.loc[(pd_df['PRIOR_3_MONTH_STORE_TXNS'] == 0),'PRIOR_3_MONTH_MKDN_AMT'] = 0

pd_df.loc[(pd_df['PRIOR_1_MONTH_STORE_TXNS'] == 0),'PRIOR_1_MONTH_TOTAL_NET_SALES'] = 0
pd_df.loc[(pd_df['PRIOR_1_MONTH_STORE_TXNS'] == 0),'PRIOR_1_MONTH_STORE_AOV'] = 0
pd_df.loc[(pd_df['PRIOR_1_MONTH_STORE_TXNS'] == 0),'PRIOR_1_MONTH_MKDN_AMT'] = 0


((pd_df[prior_txns_metrics].isna().sum()/len(pd_df)).sort_values(ascending= False))

Out[29]: PRIOR_1_MONTH_STORE_TXNS 0.0
PRIOR_1_MONTH_TOTAL_NET_SALES 0.0
PRIOR_1_MONTH_STORE_AOV 0.0
PRIOR_1_MONTH_MKDN_AMT 0.0
PRIOR_3_MONTH_STORE_TXNS 0.0
PRIOR_3_MONTH_TOTAL_NET_SALES 0.0
PRIOR_3_MONTH_STORE_AOV 0.0
PRIOR_3_MONTH_MKDN_AMT 0.0
PRIOR_1MO_CLIPPED_COUPON 0.0
PRIOR_3MO_CLIPPED_COUPON 0.0
dtype: float64

In [0]:
prior_1_month = ['PRIOR_1MO_ALCOHOLIC_BEVERAGES',
                  'PRIOR_1MO_BAKERY',
                  'PRIOR_1MO_BAKERY_PKD_OUTSIDE',
                  'PRIOR_1MO_BAR',
                  'PRIOR_1MO_CATERING',
                  'PRIOR_1MO_DAIRY',
                  'PRIOR_1MO_DELICATESSEN',
                  'PRIOR_1MO_FLORAL',
                  'PRIOR_1MO_FOOD_SERVICE',
                  'PRIOR_1MO_FRONT_END_SERVICE',
                  'PRIOR_1MO_FROZEN_GROCERY',
                  'PRIOR_1MO_FUEL_STATION',
                  'PRIOR_1MO_GM_HBC',
                  'PRIOR_1MO_GROCERY',
                  'PRIOR_1MO_JAMBA_JUICE',
                  'PRIOR_1MO_MEAT',
                  'PRIOR_1MO_PHARMACY',
                  'PRIOR_1MO_PLATED_MEAL_KITS',
                  'PRIOR_1MO_PRODUCE',
                  'PRIOR_1MO_SEAFOOD',
                  'PRIOR_1MO_STARBUCKS',
                  'PRIOR_1MO_TOBACCO',
                  'PRIOR_1MO_OWN_BRANDS_PERC',
                  'PRIOR_1MO_FRESH_SALES_PERC']

prior_3_months = ['PRIOR_3MO_ALCOHOLIC_BEVERAGES',
                  'PRIOR_3MO_BAKERY',
                  'PRIOR_3MO_BAKERY_PKD_OUTSIDE',
                  'PRIOR_3MO_BAR',
                  'PRIOR_3MO_CATERING',
                  'PRIOR_3MO_DAIRY',
                  'PRIOR_3MO_DELICATESSEN',
                  'PRIOR_3MO_FLORAL',
                  'PRIOR_3MO_FOOD_SERVICE',
                  'PRIOR_3MO_FRONT_END_SERVICE',
                  'PRIOR_3MO_FROZEN_GROCERY',
                  'PRIOR_3MO_FUEL_STATION',
                  'PRIOR_3MO_GM_HBC',
                  'PRIOR_3MO_GROCERY',
                  'PRIOR_3MO_JAMBA_JUICE',
                  'PRIOR_3MO_MEAT',
                  'PRIOR_3MO_PHARMACY',
                  'PRIOR_3MO_PLATED_MEAL_KITS',
                  'PRIOR_3MO_PRODUCE',
                  'PRIOR_3MO_SEAFOOD',
                  'PRIOR_3MO_STARBUCKS',
                  'PRIOR_3MO_TOBACCO',
                  'PRIOR_3MO_OWN_BRANDS_PERC',
                  'PRIOR_3MO_FRESH_SALES_PERC']

for x in prior_1_month:
  pd_df.loc[(pd_df['PRIOR_1_MONTH_STORE_TXNS'] >= 0)&(pd_df[x].isnull()),x] = 0
  
for x in prior_3_months:
  pd_df.loc[(pd_df['PRIOR_3_MONTH_STORE_TXNS'] >= 0)&(pd_df[x].isnull()),x] = 0

((pd_df[prior_1_month+prior_3_months].isna().sum()/len(pd_df)).sort_values(ascending= False))

Out[30]: PRIOR_1MO_ALCOHOLIC_BEVERAGES 0.0
PRIOR_1MO_BAKERY 0.0
PRIOR_3MO_BAKERY_PKD_OUTSIDE 0.0
PRIOR_3MO_BAR 0.0
PRIOR_3MO_CATERING 0.0
PRIOR_3MO_DAIRY 0.0
PRIOR_3MO_DELICATESSEN 0.0
PRIOR_3MO_FLORAL 0.0
PRIOR_3MO_FOOD_SERVICE 0.0
PRIOR_3MO_FRONT_END_SERVICE 0.0
PRIOR_3MO_FROZEN_GROCERY 0.0
PRIOR_3MO_FUEL_STATION 0.0
PRIOR_3MO_GM_HBC 0.0
PRIOR_3MO_GROCERY 0.0
PRIOR_3MO_JAMBA_JUICE 0.0
PRIOR_3MO_MEAT 0.0
PRIOR_3MO_PHARMACY 0.0
PRIOR_3MO_PLATED_MEAL_KITS 0.0
PRIOR_3MO_PRODUCE 0.0
PRIOR_3MO_SEAFOOD 0.0
PRIOR_3MO_STARBUCKS 0.0
PRIOR_3MO_TOBACCO 0.0
PRIOR_3MO_OWN_BRANDS_PERC 0.0
PRIOR_3MO_BAKERY 0.0
PRIOR_3MO_ALCOHOLIC_BEVERAGES 0.0
PRIOR_1MO_FRESH_SALES_PERC 0.0
PRIOR_1MO_FUEL_STATION 0.0
PRIOR_1MO_BAKERY_PKD_OUTSIDE 0.0
PRIOR_1MO_BAR 0.0
PRIOR_1MO_CATERING 0.0
PRIOR_1MO_DAIRY 0.0
PRIOR_1MO_DELICATESSEN 0.0
PRIOR_1MO_FLORAL 0.0
PRIOR_1MO_FOOD_SERVICE 0.0
PRIOR_1MO_FRONT_END_SERVICE 0.0
PRIOR_1MO_FROZEN_GROCERY 0.0
PRIOR_1MO_GM_HBC 0.0
PRIOR_1MO_OWN_BRANDS_PERC 0.0
PRIOR_1MO_GROCERY 0.0
PRIOR_1MO_JAMBA_JUICE 0.0
PRIOR_1MO_MEAT 0.0
PRIOR_1MO_PHARMACY 0.0
PRIOR_1MO_PLATED_MEAL_KITS 0.0
PRIOR_1MO_PRODUCE 0.0
PRIOR_1MO_SEAFOOD 0.0
PRIOR_1MO_STARBUCKS 0.0
PRIOR_1MO_TOBACCO 0.0
PRIOR_3MO_FRESH_SALES_PERC 0.0
dtype: float64

##### Numerical Columns

In [0]:
((pd_df[['AVG_SOOS','ECOM_TXNCOUNTPERWEEK','ECOM_AOV']].isna().sum()/len(pd_df)).sort_values(ascending= False))

Out[31]: AVG_SOOS 0.029845
ECOM_TXNCOUNTPERWEEK 0.029234
ECOM_AOV 0.029234
dtype: float64

In [0]:
pd_df[['AVG_SOOS','ECOM_TXNCOUNTPERWEEK','ECOM_AOV']].describe()

Out[32]:

AVG_SOOS 
 ECOM_TXNCOUNTPERWEEK 
 ECOM_AOV 
 
 
 
 
 count 
 8.808127e+06 
 8.813675e+06 
 8.813675e+06 
 
 
 mean 
 8.234803e-02 
 2.306758e+02 
 9.101535e+01 
 
 
 std 
 8.495717e-02 
 1.976304e+02 
 1.268658e+01 
 
 
 min 
 0.000000e+00 
 8.461540e-01 
 5.842218e+01 
 
 
 25% 
 1.743600e-02 
 1.116923e+02 
 8.241603e+01 
 
 
 50% 
 5.837423e-02 
 1.893077e+02 
 8.998822e+01 
 
 
 75% 
 1.199095e-01 
 3.029231e+02 
 9.819818e+01 
 
 
 max 
 5.491950e-01 
 2.393077e+03 
 1.598083e+02

In [0]:
cols = ['AVG_SOOS','ECOM_TXNCOUNTPERWEEK','ECOM_AOV']
df_out = percent_outliers(pd_df,cols)
df_out

Out[33]:

Column 
 IQR_LOutlier 
 IQR_ROutlier 
 Sigma_LOutlier 
 Sigma_ROutlier 
 
 
 
 
 0 
 AVG_SOOS 
 0.000000 
 0.041119 
 0.0 
 0.00000 
 
 
 1 
 ECOM_TXNCOUNTPERWEEK 
 0.000000 
 0.031063 
 0.0 
 0.00312 
 
 
 2 
 ECOM_AOV 
 0.000838 
 0.016697 
 0.0 
 0.00000

In [0]:
pd_df = remove_outlier(pd_df,cols, pd_df)
pd_df[cols].describe()

Out[34]:

AVG_SOOS 
 ECOM_TXNCOUNTPERWEEK 
 ECOM_AOV 
 
 
 
 
 count 
 8.808127e+06 
 8.813675e+06 
 8.813675e+06 
 
 
 mean 
 8.234803e-02 
 2.283135e+02 
 9.101535e+01 
 
 
 std 
 8.495717e-02 
 1.774721e+02 
 1.268658e+01 
 
 
 min 
 0.000000e+00 
 8.461540e-01 
 5.842218e+01 
 
 
 25% 
 1.743600e-02 
 1.116923e+02 
 8.241603e+01 
 
 
 50% 
 5.837423e-02 
 1.893077e+02 
 8.998822e+01 
 
 
 75% 
 1.199095e-01 
 3.029231e+02 
 9.819818e+01 
 
 
 max 
 5.491950e-01 
 1.416458e+03 
 1.598083e+02

In [0]:
for x in cols:
  pd_df.loc[(pd_df[x].isnull()), x] = pd_df[x].median()

((pd_df[cols].isna().sum()/len(pd_df)).sort_values(ascending= False))

Out[35]: AVG_SOOS 0.0
ECOM_TXNCOUNTPERWEEK 0.0
ECOM_AOV 0.0
dtype: float64

##### Categorical columns

In [0]:
((pd_df[['MF_MY_NEEDS_SEGMENT','MF_TRUPRICE_SEGMENT','MF_SHOP_STYLE_SEG_SEGMENT','MF_FACTS_SEGMENT_NAME','CLUSTER']].isna().sum()/len(pd_df)).sort_values(ascending= False))


Out[36]: MF_MY_NEEDS_SEGMENT 0.005313
CLUSTER 0.003016
MF_TRUPRICE_SEGMENT 0.000910
MF_SHOP_STYLE_SEG_SEGMENT 0.000910
MF_FACTS_SEGMENT_NAME 0.000910
dtype: float64

In [0]:
pd_df[['MF_MY_NEEDS_SEGMENT','MF_TRUPRICE_SEGMENT','MF_SHOP_STYLE_SEG_SEGMENT','MF_FACTS_SEGMENT_NAME','CLUSTER']].describe()

Out[37]:

MF_MY_NEEDS_SEGMENT 
 MF_TRUPRICE_SEGMENT 
 MF_SHOP_STYLE_SEG_SEGMENT 
 MF_FACTS_SEGMENT_NAME 
 CLUSTER 
 
 
 
 
 count 
 9030857 
 9070829 
 9070829 
 9070829 
 9051708 
 
 
 unique 
 6 
 6 
 7 
 5 
 11 
 
 
 top 
 Scratch Foodies 
 Quality Driven 
 COOKING FROM SCRATCH 
 3.Good 
 High Mainstream 
 
 
 freq 
 2795162 
 1680663 
 2146023 
 4031914 
 2391193

In [0]:
# For categorical data points - imputing with mode
cat_cols = ['MF_MY_NEEDS_SEGMENT','MF_TRUPRICE_SEGMENT','MF_SHOP_STYLE_SEG_SEGMENT','MF_FACTS_SEGMENT_NAME','CLUSTER']

for x in cat_cols:
  pd_df.loc[(pd_df[x].isnull()), x] = pd_df[x].mode().item()

((pd_df[cat_cols].isna().sum()/len(pd_df)).sort_values(ascending= False))

Out[38]: MF_MY_NEEDS_SEGMENT 0.0
MF_TRUPRICE_SEGMENT 0.0
MF_SHOP_STYLE_SEG_SEGMENT 0.0
MF_FACTS_SEGMENT_NAME 0.0
CLUSTER 0.0
dtype: float64

In [0]:
pd_df.loc[(pd_df['NPS_NPS_LAST_4_WEEKS_FOR_ELITE_BEST'].isnull()), 'NPS_NPS_LAST_4_WEEKS_FOR_ELITE_BEST'] = pd_df['NPS_NPS_LAST_4_WEEKS_FOR_ELITE_BEST'].median()
pd_df.loc[(pd_df['IRI_SALES_SALES_PER_SQ_FT'].isnull()), 'IRI_SALES_SALES_PER_SQ_FT'] = pd_df['IRI_SALES_SALES_PER_SQ_FT'].median()
pd_df.loc[(pd_df['NPS_NPS_YTD_FOR_ELITE_BEST'].isnull()), 'NPS_NPS_YTD_FOR_ELITE_BEST'] = pd_df['NPS_NPS_YTD_FOR_ELITE_BEST'].median()

((pd_df.isna().sum()/len(pd_df)).sort_values(ascending= False)).head(50)

Out[39]: MFC 1.000000
EBIDTA_EBIDTA_DOLLAR_TY 1.000000
EBIDTA_EBIDTA_DOLLAR_CHANGE 1.000000
EBIDTA_EBIDTA_PER_CHANGE_IN_PTS 1.000000
EBIDTA_EBIDTA_PER_TY 1.000000
OFFERINGS_PHARMACY_SALES_GROWTH_PER 0.201314
MSA 0.098704
LAST_REMODEL_AMOUNT 0.081911
LAST_REMODEL_DATE 0.081911
ECOM_SALES 0.029234
ECOM_TXN_COUNT 0.029234
LAST_INSTORE_TXN_DTE_PRETP 0.023904
AGE_35_44_TRADE_AREA_PER 0.000000
AGE_35_44_STORE_PER 0.000000
AGE_35_44_VARIANCE_IN_PTS 0.000000
AGE_45_54_STORE_PER 0.000000
AGE_45_54_TRADE_AREA_PER 0.000000
AGE_45_54_VARIANCE_IN_PTS 0.000000
AGE_25_34_VARIANCE_IN_PTS 0.000000
AGE_25_34_TRADE_AREA_PER 0.000000
HHS_ID 0.000000
AGE_55_64_STORE_PER 0.000000
AGE_15_24_VARIANCE_IN_PTS 0.000000
AGE_55_64_TRADE_AREA_PER 0.000000
AGE_55_64_VARIANCE_IN_PTS 0.000000
AGE_65_74_STORE_PER 0.000000
AGE_65_74_TRADE_AREA_PER 0.000000
AGE_65_74_VARIANCE_IN_PTS 0.000000
AGE_75_OR_MORE_STORE_PER 0.000000
AGE_75_OR_MORE_TRADE_AREA_PER 0.000000
AGE_75_OR_MORE_VARIANCE_IN_PTS 0.000000
INCOME_LESS_THAN_10K_STORE_PER 0.000000
INCOME_LESS_THAN_10K_TRADE_AREA_PER 0.000000
INCOME_LESS_THAN_10K_VARIANCE_IN_PTS 0.000000
INCOME_10K_25K_STORE_PER 0.000000
INCOME_10K_25K_TRADE_AREA_PER 0.000000
INCOME_10K_25K_VARIANCE_IN_PTS 0.000000
AGE_25_34_STORE_PER 0.000000
MYNEEDS_SCRATCH_FOODIES_PER_OF_SALES 0.000000
AGE_15_24_TRADE_AREA_PER 0.000000
TRUPRICE_QUALITY_DRIVEN_PER_OF_SALES 0.000000
AIV_AIV_PER_CHANGE 0.000000
MARKDOWN_MARKDOWN_PER 0.000000
HH_COUNTS_HH_COUNT_TY 0.000000
HH_COUNTS_HH_COUNT_PER_CHANGE 0.000000
SNAP_PER_OF_SALES_FROM_SNAP 0.000000
OTHER_PER_HH_REDEEMING_J4U_OFFERS 0.000000
FACTS_ELITEBEST_PER_OF_SALES 0.000000
FACTS_GOOD_PER_OF_SALES 0.000000
FACTS_OCCASIONAL_PER_OF_SALES 0.000000
dtype: float64

## 3.d  Generation of pd_df_valid DF

In [0]:
# Remove the metrics which has >=98% of missing values - We'll use these metrics for bivariate analysis for sure
high_missing = ['MFC','EBIDTA_EBIDTA_PER_CHANGE_IN_PTS','EBIDTA_EBIDTA_PER_TY','EBIDTA_EBIDTA_DOLLAR_CHANGE','EBIDTA_EBIDTA_DOLLAR_TY','OFFERINGS_PHARMACY_SALES_GROWTH_PER','MSA','ECOM_SALES','ECOM_TXN_COUNT','LAST_INSTORE_TXN_DTE_PRETP','LAST_REMODEL_AMOUNT','LAST_REMODEL_DATE']
pd_df_valid = pd_df.drop(high_missing, axis=1)

In [0]:
intermediate_cols_remove = ['BANNER','DISTRICT','DIVISION']
pd_df_valid = pd_df_valid.drop(intermediate_cols_remove, axis=1)
pd_df_valid.shape

Out[41]: (9079095, 240)

In [0]:
(pd_df_valid.isna().sum()/len(pd_df_valid)).sort_values(ascending= False).head(50)

Out[42]: HHS_ID 0.0
FRST_INSTORE_TXN_DTE 0.0
MYNEEDS_EASY_SHOPPING_PER_OF_SALES 0.0
AGE_15_24_STORE_PER 0.0
AGE_15_24_TRADE_AREA_PER 0.0
AGE_15_24_VARIANCE_IN_PTS 0.0
AGE_25_34_STORE_PER 0.0
AGE_25_34_TRADE_AREA_PER 0.0
AGE_25_34_VARIANCE_IN_PTS 0.0
AGE_35_44_STORE_PER 0.0
AGE_35_44_TRADE_AREA_PER 0.0
AGE_35_44_VARIANCE_IN_PTS 0.0
AGE_45_54_STORE_PER 0.0
AGE_45_54_TRADE_AREA_PER 0.0
AGE_45_54_VARIANCE_IN_PTS 0.0
AGE_55_64_STORE_PER 0.0
AGE_55_64_TRADE_AREA_PER 0.0
AGE_55_64_VARIANCE_IN_PTS 0.0
AGE_65_74_STORE_PER 0.0
AGE_65_74_TRADE_AREA_PER 0.0
AGE_65_74_VARIANCE_IN_PTS 0.0
AGE_75_OR_MORE_STORE_PER 0.0
AGE_75_OR_MORE_TRADE_AREA_PER 0.0
AGE_75_OR_MORE_VARIANCE_IN_PTS 0.0
INCOME_LESS_THAN_10K_STORE_PER 0.0
INCOME_LESS_THAN_10K_TRADE_AREA_PER 0.0
INCOME_LESS_THAN_10K_VARIANCE_IN_PTS 0.0
INCOME_10K_25K_STORE_PER 0.0
INCOME_10K_25K_TRADE_AREA_PER 0.0
MYNEEDS_SCRATCH_FOODIES_PER_OF_SALES 0.0
MYNEEDS_CHASING_PRICE_PER_OF_SALES 0.0
MYNEEDS_HEALTHY_FOODIES_PER_OF_SALES 0.0
FACTS_GOOD_PER_OF_SALES 0.0
SPACE_ALLOCATION_GM_HBC 0.0
SPACE_ALLOCATION_GROCERY 0.0
SPACE_ALLOCATION_OTHERS 0.0
SPACE_ALLOCATION_PKGD_BAKERY 0.0
AIV_AIV_TY 0.0
AIV_AIV_PER_CHANGE 0.0
MARKDOWN_MARKDOWN_PER 0.0
HH_COUNTS_HH_COUNT_TY 0.0
HH_COUNTS_HH_COUNT_PER_CHANGE 0.0
SNAP_PER_OF_SALES_FROM_SNAP 0.0
OTHER_PER_HH_REDEEMING_J4U_OFFERS 0.0
FACTS_ELITEBEST_PER_OF_SALES 0.0
FACTS_OCCASIONAL_PER_OF_SALES 0.0
MYNEEDS_ONE_STOP_LOW_PRICE_PER_OF_SALES 0.0
TRUPRICE_MOST_PRICE_DRIVEN_PER_OF_SALES 0.0
TRUPRICE_PRICE_DRIVEN_PER_OF_SALES 0.0
TRUPRICE_PRICE_NEUTRAL_PER_OF_SALES 0.0
dtype: float64

In [0]:
# Columns having nas
nacols = pd_df_valid.loc[:, (pd_df_valid.isnull().sum(axis=0) > 0)].columns
print(len(nacols), nacols)

0 Index([], dtype='object')

In [0]:
bcols = pd_df_valid.select_dtypes('bool').columns.to_list()
print('Boolean columns: ',len(bcols))

dtcols = pd_df_valid.select_dtypes('datetime').columns.to_list()
print('Datetime columns: ',len(dtcols))

f32cols = pd_df_valid.select_dtypes('float32').columns.to_list()
f64cols = pd_df_valid.select_dtypes('float64').columns.to_list()
intcols = pd_df_valid.select_dtypes('int32').columns.to_list()
ficols = f32cols + f64cols + intcols
print('Float columns: ',len(ficols))

string_columns = pd_df_valid.select_dtypes('object').columns.to_list()
print('String columns: ',len(string_columns))

Boolean columns: 5
Datetime columns: 0
Float columns: 216
String columns: 19

In [0]:
outlier_treated_cols = ['AVG_SOOS','ECOM_TXNCOUNTPERWEEK','ECOM_AOV']
outlier_treatment_required = ficols

for x in outlier_treated_cols:
  if x in outlier_treatment_required:
    outlier_treatment_required.remove(x)
print(len(outlier_treatment_required))

213

#### Outlier treatment for overall metrics

In [0]:
df_out = percent_outliers(pd_df_valid,outlier_treatment_required)
df_out

Out[46]:

Column 
 IQR_LOutlier 
 IQR_ROutlier 
 Sigma_LOutlier 
 Sigma_ROutlier 
 
 
 
 
 0 
 TXN_COUNT 
 0.000000 
 0.074129 
 0.0 
 4.405725e-07 
 
 
 1 
 TOTAL_NET_SALES 
 0.000000 
 0.078009 
 0.0 
 4.405725e-07 
 
 
 2 
 AOV 
 0.000000 
 0.056743 
 0.0 
 1.919354e-03 
 
 
 3 
 PRIOR_1_MONTH_STORE_TXNS 
 0.000000 
 0.056107 
 0.0 
 5.507157e-07 
 
 
 4 
 PRIOR_1_MONTH_TOTAL_NET_SALES 
 0.000000 
 0.074197 
 0.0 
 4.405725e-07 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 208 
 INSTORE_SALES 
 0.000000 
 0.033075 
 0.0 
 0.000000e+00 
 
 
 209 
 INSTORE_TXN_COUNT 
 0.000000 
 0.023173 
 0.0 
 0.000000e+00 
 
 
 210 
 INSTORE_AOV 
 0.001736 
 0.013056 
 0.0 
 0.000000e+00 
 
 
 211 
 INSTORE_TXNCOUNTPERWEEK 
 0.000000 
 0.023173 
 0.0 
 0.000000e+00 
 
 
 212 
 DR_CUSTOMER 
 0.000000 
 0.000000 
 0.0 
 0.000000e+00 
 
 
 
 213 rows × 5 columns

In [0]:
pd_df_valid = remove_outlier(pd_df_valid,outlier_treatment_required, pd_df_valid)

# 4. Do additional EDA

## 4.a Dpt Cols

In [0]:
for x in prior_1_month+prior_3_months:
  pd_df_valid.loc[(pd_df_valid[x]<0),x] = 0
  pd_df_valid.loc[(pd_df_valid[x]>100),x] = 100

In [0]:
dpt_res = pd.DataFrame(columns=['Feature','Less than 100','Greater than 100'])
for x in prior_1_month+prior_3_months:
  neg = (len(pd_df_valid[pd_df_valid[x]<0])/len(pd_df_valid))*100
  pos = (len(pd_df_valid[pd_df_valid[x]>100])/len(pd_df_valid))*100
  dpt_res.loc[len(dpt_res)] = [x,neg,pos]
  
dpt_res

Out[49]:

Feature 
 Less than 100 
 Greater than 100 
 
 
 
 
 0 
 PRIOR_1MO_ALCOHOLIC_BEVERAGES 
 0.0 
 0.0 
 
 
 1 
 PRIOR_1MO_BAKERY 
 0.0 
 0.0 
 
 
 2 
 PRIOR_1MO_BAKERY_PKD_OUTSIDE 
 0.0 
 0.0 
 
 
 3 
 PRIOR_1MO_BAR 
 0.0 
 0.0 
 
 
 4 
 PRIOR_1MO_CATERING 
 0.0 
 0.0 
 
 
 5 
 PRIOR_1MO_DAIRY 
 0.0 
 0.0 
 
 
 6 
 PRIOR_1MO_DELICATESSEN 
 0.0 
 0.0 
 
 
 7 
 PRIOR_1MO_FLORAL 
 0.0 
 0.0 
 
 
 8 
 PRIOR_1MO_FOOD_SERVICE 
 0.0 
 0.0 
 
 
 9 
 PRIOR_1MO_FRONT_END_SERVICE 
 0.0 
 0.0 
 
 
 10 
 PRIOR_1MO_FROZEN_GROCERY 
 0.0 
 0.0 
 
 
 11 
 PRIOR_1MO_FUEL_STATION 
 0.0 
 0.0 
 
 
 12 
 PRIOR_1MO_GM_HBC 
 0.0 
 0.0 
 
 
 13 
 PRIOR_1MO_GROCERY 
 0.0 
 0.0 
 
 
 14 
 PRIOR_1MO_JAMBA_JUICE 
 0.0 
 0.0 
 
 
 15 
 PRIOR_1MO_MEAT 
 0.0 
 0.0 
 
 
 16 
 PRIOR_1MO_PHARMACY 
 0.0 
 0.0 
 
 
 17 
 PRIOR_1MO_PLATED_MEAL_KITS 
 0.0 
 0.0 
 
 
 18 
 PRIOR_1MO_PRODUCE 
 0.0 
 0.0 
 
 
 19 
 PRIOR_1MO_SEAFOOD 
 0.0 
 0.0 
 
 
 20 
 PRIOR_1MO_STARBUCKS 
 0.0 
 0.0 
 
 
 21 
 PRIOR_1MO_TOBACCO 
 0.0 
 0.0 
 
 
 22 
 PRIOR_1MO_OWN_BRANDS_PERC 
 0.0 
 0.0 
 
 
 23 
 PRIOR_1MO_FRESH_SALES_PERC 
 0.0 
 0.0 
 
 
 24 
 PRIOR_3MO_ALCOHOLIC_BEVERAGES 
 0.0 
 0.0 
 
 
 25 
 PRIOR_3MO_BAKERY 
 0.0 
 0.0 
 
 
 26 
 PRIOR_3MO_BAKERY_PKD_OUTSIDE 
 0.0 
 0.0 
 
 
 27 
 PRIOR_3MO_BAR 
 0.0 
 0.0 
 
 
 28 
 PRIOR_3MO_CATERING 
 0.0 
 0.0 
 
 
 29 
 PRIOR_3MO_DAIRY 
 0.0 
 0.0 
 
 
 30 
 PRIOR_3MO_DELICATESSEN 
 0.0 
 0.0 
 
 
 31 
 PRIOR_3MO_FLORAL 
 0.0 
 0.0 
 
 
 32 
 PRIOR_3MO_FOOD_SERVICE 
 0.0 
 0.0 
 
 
 33 
 PRIOR_3MO_FRONT_END_SERVICE 
 0.0 
 0.0 
 
 
 34 
 PRIOR_3MO_FROZEN_GROCERY 
 0.0 
 0.0 
 
 
 35 
 PRIOR_3MO_FUEL_STATION 
 0.0 
 0.0 
 
 
 36 
 PRIOR_3MO_GM_HBC 
 0.0 
 0.0 
 
 
 37 
 PRIOR_3MO_GROCERY 
 0.0 
 0.0 
 
 
 38 
 PRIOR_3MO_JAMBA_JUICE 
 0.0 
 0.0 
 
 
 39 
 PRIOR_3MO_MEAT 
 0.0 
 0.0 
 
 
 40 
 PRIOR_3MO_PHARMACY 
 0.0 
 0.0 
 
 
 41 
 PRIOR_3MO_PLATED_MEAL_KITS 
 0.0 
 0.0 
 
 
 42 
 PRIOR_3MO_PRODUCE 
 0.0 
 0.0 
 
 
 43 
 PRIOR_3MO_SEAFOOD 
 0.0 
 0.0 
 
 
 44 
 PRIOR_3MO_STARBUCKS 
 0.0 
 0.0 
 
 
 45 
 PRIOR_3MO_TOBACCO 
 0.0 
 0.0 
 
 
 46 
 PRIOR_3MO_OWN_BRANDS_PERC 
 0.0 
 0.0 
 
 
 47 
 PRIOR_3MO_FRESH_SALES_PERC 
 0.0 
 0.0

## 4.b Banner Names

In [0]:
pd_df_valid['LU_BANNER'] = pd_df_valid['LU_BANNER'].apply(str.upper)

pd_df_valid.loc[(pd_df_valid['LU_BANNER'] == 'PAK N SAV'), 'LU_BANNER'] = 'SAFEWAY'
pd_df_valid.loc[(pd_df_valid['LU_BANNER'] == 'MARKET STREET IMT'), 'LU_BANNER'] = 'ALBERTSONS'

pd_df_valid['LU_BANNER'].unique()

Out[50]: array(['SAFEWAY', 'ACME', 'ALBERTSONS', 'TOM THUMB', 'VONS', 'JEWEL-OSCO',
 "SHAW'S", 'RANDALLS', "BALDUCCI'S", 'STAR MARKET', 'KINGS',
 'PAVILIONS', 'CARRS', 'HAGGEN', 'ANDRONICO’S', 'LUCKY'],
 dtype=object)

In [0]:
#HOUSEHOLD_ID
#Check what all features to remove
#Mostly features which has no importance like storeid, txnid, orderdate and those which has unbalanced data (99-1%) distribution, they are removed here
cols_to_remove = ['LU_DISTRICT','STORE_ID','ADDRESS','CITY','STATE']

pd_df_valid = pd_df_valid.drop(cols_to_remove, axis=1)

In [0]:
print(pd_df_valid.shape)

bcols = pd_df_valid.select_dtypes('bool').columns.to_list()
print('Boolean columns: ',len(bcols))

dtcols = pd_df_valid.select_dtypes('datetime').columns.to_list()
print('Datetime columns: ',len(dtcols))

f32cols = pd_df_valid.select_dtypes('float32').columns.to_list()
f64cols = pd_df_valid.select_dtypes('float64').columns.to_list()
intcols = pd_df_valid.select_dtypes('int32').columns.to_list()
corr_cols = f32cols + f64cols + intcols
print('Float columns: ',len(corr_cols))

string_columns = pd_df_valid.select_dtypes('object').columns.to_list()
print('String columns: ',len(string_columns))

(9079095, 235)
Boolean columns: 5
Datetime columns: 0
Float columns: 216
String columns: 14

## 4.c Store Age and Income features

In [0]:
#Create aggregated columns for Income and Age
#Income columns
income_cols = [
  'INCOME_LESS_THAN_10K_STORE_PER',
  'INCOME_10K_25K_STORE_PER',
  'INCOME_30K_40K_STORE_PER',
  'INCOME_40K_50K_STORE_PER',
  'INCOME_50K_75K_STORE_PER',
  'INCOME_75K_100K_STORE_PER',
  'INCOME_100K_150K_STORE_PER',
  'INCOME_150K_200K_STORE_PER',
  'INCOME_200K_OR_MORE_STORE_PER'
  ]

pd_df_valid['Income_UND50K_Low'] = pd_df_valid['INCOME_LESS_THAN_10K_STORE_PER'] + pd_df_valid['INCOME_10K_25K_STORE_PER'] + pd_df_valid['INCOME_30K_40K_STORE_PER'] + pd_df_valid['INCOME_40K_50K_STORE_PER']
pd_df_valid['Income_50+_100K_Medium'] = pd_df_valid['INCOME_50K_75K_STORE_PER'] + pd_df_valid['INCOME_75K_100K_STORE_PER']
pd_df_valid['Income_100+_150K_High'] =  pd_df_valid['INCOME_100K_150K_STORE_PER']
pd_df_valid['Income_150K_VeryHigh'] = pd_df_valid['INCOME_150K_200K_STORE_PER'] + pd_df_valid['INCOME_200K_OR_MORE_STORE_PER']

age_cols = [
  'AGE_15_24_STORE_PER',
  'AGE_25_34_STORE_PER',
  'AGE_35_44_STORE_PER',
  'AGE_45_54_STORE_PER',
  'AGE_55_64_STORE_PER',
  'AGE_65_74_STORE_PER',
  'AGE_75_OR_MORE_STORE_PER']

pd_df_valid['Age_UND35_Low'] = pd_df_valid['AGE_15_24_STORE_PER'] + pd_df_valid['AGE_25_34_STORE_PER']
pd_df_valid['Age35+_55_Medium'] = pd_df_valid['AGE_35_44_STORE_PER'] + pd_df_valid['AGE_45_54_STORE_PER']
pd_df_valid['Age55+_High'] = pd_df_valid['AGE_55_64_STORE_PER'] + pd_df_valid['AGE_65_74_STORE_PER'] + pd_df_valid['AGE_75_OR_MORE_STORE_PER']


In [0]:
#Create a list of columns with newly created aggregated columns
aggregated_cols = []
for x in pd_df_valid.columns.tolist():
  if x.endswith('Low') or x.endswith('Medium') or x.endswith('High'):
    aggregated_cols.append(x)

print(aggregated_cols)

store_req_features_3l = ['PERFORMANCE_DECILE','COMPETITION_NUMBER_OF_COMPETITORS','FOOT_TRAFFIC_FOOT_TRAFFIC','SNAP_PER_OF_SALES_FROM_SNAP','I_SALES_PER','U_SALES_PER','D_SALES_PER','NPS_NPS_YTD','BUILDING_SIZE_SQ_FT'] + aggregated_cols

#We will use 3 and 5 quartiles to divide these column values (q1,q2,q3,q4,q5)
print('3 levels')
for i in store_req_features_3l: 
  print(i)
  subset2 = pd_df_valid[(pd_df_valid[i]==0)] 
  subset3 = pd_df_valid[(pd_df_valid[i]!=0)]

  subset2[i] = 'q0'
  if len(subset3) == 1:
    subset3[i] = 'q1'
  elif len(subset3)>1:
    subset3[i] = pd.qcut(subset3[i].rank(method='first'), 3, ['q1','q2','q3'])

  pd_df_valid[i+'_q'] = subset2[i].append(subset3[i], ignore_index=False)

#Wherever there is q3, mark it as 1 else 0
for x in aggregated_cols:
  col_name = str(x)+'_q'
  print(col_name)
  pd_df_valid[col_name] = pd_df_valid[col_name].astype(str)
  pd_df_valid.loc[pd_df_valid[col_name] != 'q3',col_name] = 'False'
  pd_df_valid.loc[pd_df_valid[col_name] == 'q3',col_name] = '3'

pd_df_valid.drop(columns=store_req_features_3l+age_cols + income_cols,inplace=True)

pd_df_valid.head()

['Income_UND50K_Low', 'Income_50+_100K_Medium', 'Income_100+_150K_High', 'Income_150K_VeryHigh', 'Age_UND35_Low', 'Age35+_55_Medium', 'Age55+_High']
3 levels
PERFORMANCE_DECILE
COMPETITION_NUMBER_OF_COMPETITORS
FOOT_TRAFFIC_FOOT_TRAFFIC
SNAP_PER_OF_SALES_FROM_SNAP
I_SALES_PER
U_SALES_PER
D_SALES_PER
NPS_NPS_YTD
BUILDING_SIZE_SQ_FT
Income_UND50K_Low
Income_50+_100K_Medium
Income_100+_150K_High
Income_150K_VeryHigh
Age_UND35_Low
Age35+_55_Medium
Age55+_High
Income_UND50K_Low_q
Income_50+_100K_Medium_q
Income_100+_150K_High_q
Income_150K_VeryHigh_q
Age_UND35_Low_q
Age35+_55_Medium_q
Age55+_High_q
Out[54]:

HHS_ID 
 FRST_INSTORE_TXN_DTE 
 LAST_INSTORE_TXN_DTE 
 TXN_COUNT 
 TOTAL_NET_SALES 
 AOV 
 PRIOR_1_MONTH_STORE_TXNS 
 PRIOR_1_MONTH_TOTAL_NET_SALES 
 PRIOR_1_MONTH_STORE_AOV 
 PRIOR_1_MONTH_MKDN_AMT 
 PRIOR_3_MONTH_STORE_TXNS 
 PRIOR_3_MONTH_TOTAL_NET_SALES 
 PRIOR_3_MONTH_STORE_AOV 
 PRIOR_3_MONTH_MKDN_AMT 
 PRIOR_1MO_CLIPPED_COUPON 
 PRIOR_3MO_CLIPPED_COUPON 
 INSTORE_TXN_ID_INIT 
 INSTORE_STORE_ID_INIT 
 INSTORE_TXN_ID_LAST 
 INSTORE_STORE_ID_LAST 
 DR_CUSTOMER 
 PRIOR_1MO_ALCOHOLIC_BEVERAGES 
 PRIOR_1MO_BAKERY 
 PRIOR_1MO_BAKERY_PKD_OUTSIDE 
 PRIOR_1MO_BAR 
 PRIOR_1MO_CATERING 
 PRIOR_1MO_DAIRY 
 PRIOR_1MO_DELICATESSEN 
 PRIOR_1MO_FLORAL 
 PRIOR_1MO_FOOD_SERVICE 
 PRIOR_1MO_FRONT_END_SERVICE 
 PRIOR_1MO_FROZEN_GROCERY 
 PRIOR_1MO_FUEL_STATION 
 PRIOR_1MO_GM_HBC 
 PRIOR_1MO_GROCERY 
 PRIOR_1MO_JAMBA_JUICE 
 PRIOR_1MO_MEAT 
 PRIOR_1MO_PHARMACY 
 PRIOR_1MO_PLATED_MEAL_KITS 
 PRIOR_1MO_PRODUCE 
 ... 
 ETHNICITY_HISPANIC_TRADE_AREA_PER 
 ETHNICITY_HISPANIC_VARIANCE_IN_PTS 
 ETHNICITY_OTHER_STORE_PER 
 ETHNICITY_OTHE_TRADE_AREAR_PER 
 ETHNICITY_OTHER_VARIANCE_IN_PTS 
 CLUSTER 
 URBANICITY 
 STARBUCKS 
 INSTACART 
 FUEL 
 PHARMACY 
 DUG 
 HOME_DELIVERY 
 SELLING_AREA_SQ_FT 
 LU_BANNER 
 LU_DIVISION 
 AVG_SOOS 
 ECOM_AOV 
 ECOM_TXNCOUNTPERWEEK 
 INSTORE_SALES 
 INSTORE_TXN_COUNT 
 INSTORE_AOV 
 INSTORE_TXNCOUNTPERWEEK 
 EMP_FLAG 
 PERFORMANCE_DECILE_q 
 COMPETITION_NUMBER_OF_COMPETITORS_q 
 FOOT_TRAFFIC_FOOT_TRAFFIC_q 
 SNAP_PER_OF_SALES_FROM_SNAP_q 
 I_SALES_PER_q 
 U_SALES_PER_q 
 D_SALES_PER_q 
 NPS_NPS_YTD_q 
 BUILDING_SIZE_SQ_FT_q 
 Income_UND50K_Low_q 
 Income_50+_100K_Medium_q 
 Income_100+_150K_High_q 
 Income_150K_VeryHigh_q 
 Age_UND35_Low_q 
 Age35+_55_Medium_q 
 Age55+_High_q 
 
 
 
 
 0 
 250013853375 
 2023-09-01 
 2023-11-08 
 9.0 
 179.940002 
 19.993334 
 3.0 
 44.169998 
 14.723333 
 -0.990000 
 9.0 
 142.279999 
 15.808888 
 -0.882222 
 0.0 
 0.0 
 5.771579e+09 
 970.0 
 6.187555e+09 
 970.0 
 1.0 
 0.000000 
 12.076318 
 0.000000 
 0.0 
 0.0 
 11.200897 
 20.179573 
 0.0 
 0.000000 
 0.000000 
 0.000000 
 0.0 
 0.000000 
 11.290684 
 0.0 
 6.711560 
 0.0 
 0.0 
 38.540966 
 ... 
 0.16 
 1.0 
 0.06 
 0.05 
 1.0 
 Medium Premium 
 Urban 
 True 
 True 
 False 
 True 
 Y 
 Y 
 30002.0 
 SAFEWAY 
 NOR. CALIFORNIA 
 0.013575 
 85.379433 
 105.153847 
 11236189.0 
 318114.0 
 35.321266 
 24470.308594 
 False 
 q1 
 q3 
 q3 
 q2 
 q3 
 q1 
 q2 
 q3 
 q1 
 False 
 False 
 False 
 3 
 False 
 False 
 False 
 
 
 1 
 990056121312 
 2023-08-23 
 2023-11-10 
 6.0 
 837.859985 
 139.643326 
 1.0 
 316.339996 
 284.757721 
 -27.420000 
 5.0 
 793.159973 
 158.632004 
 -19.573999 
 0.0 
 0.0 
 5.714301e+09 
 3735.0 
 6.195261e+09 
 3798.0 
 1.0 
 0.000000 
 1.825971 
 1.199028 
 0.0 
 0.0 
 5.044277 
 7.666988 
 0.0 
 0.000000 
 13.061309 
 8.325278 
 0.0 
 7.959562 
 45.280949 
 0.0 
 8.738016 
 0.0 
 0.0 
 0.898618 
 ... 
 0.03 
 0.0 
 0.05 
 0.03 
 2.0 
 High Mainstream 
 Suburban 
 False 
 True 
 False 
 True 
 Y 
 Y 
 0.0 
 ACME 
 MID-ATLANTIC 
 0.068910 
 106.195938 
 60.076923 
 6558639.0 
 175464.0 
 37.378830 
 13497.230469 
 False 
 q1 
 q3 
 q1 
 q2 
 q3 
 q1 
 q1 
 q1 
 q2 
 False 
 False 
 3 
 3 
 False 
 False 
 3 
 
 
 2 
 990031543568 
 2023-08-17 
 2023-11-11 
 16.0 
 428.320007 
 26.770000 
 4.0 
 103.300003 
 25.825001 
 -4.387500 
 15.0 
 417.329987 
 27.822001 
 -7.337333 
 0.0 
 2.0 
 5.676692e+09 
 2428.0 
 6.202629e+09 
 2428.0 
 1.0 
 0.000000 
 0.000000 
 3.136119 
 0.0 
 0.0 
 13.380223 
 16.541166 
 0.0 
 5.370293 
 0.000000 
 0.000000 
 0.0 
 0.000000 
 61.572197 
 0.0 
 0.000000 
 0.0 
 0.0 
 0.000000 
 ... 
 0.12 
 -2.0 
 0.05 
 0.03 
 2.0 
 High Mainstream 
 Rural 
 False 
 True 
 False 
 True 
 Y 
 Y 
 0.0 
 ACME 
 MID-ATLANTIC 
 0.000000 
 107.845436 
 142.538467 
 6568394.5 
 151004.0 
 43.498150 
 11615.692383 
 False 
 q1 
 q2 
 q1 
 q1 
 q3 
 q2 
 q2 
 q3 
 q1 
 False 
 False 
 3 
 3 
 False 
 False 
 False 
 
 
 3 
 990033666462 
 2023-08-16 
 2023-11-14 
 38.0 
 526.159973 
 13.846315 
 

In [0]:
display(pd_df_valid.head())

HHS_ID FRST_INSTORE_TXN_DTE LAST_INSTORE_TXN_DTE TXN_COUNT TOTAL_NET_SALES AOV PRIOR_1_MONTH_STORE_TXNS PRIOR_1_MONTH_TOTAL_NET_SALES PRIOR_1_MONTH_STORE_AOV PRIOR_1_MONTH_MKDN_AMT PRIOR_3_MONTH_STORE_TXNS PRIOR_3_MONTH_TOTAL_NET_SALES PRIOR_3_MONTH_STORE_AOV PRIOR_3_MONTH_MKDN_AMT PRIOR_1MO_CLIPPED_COUPON PRIOR_3MO_CLIPPED_COUPON INSTORE_TXN_ID_INIT INSTORE_STORE_ID_INIT INSTORE_TXN_ID_LAST INSTORE_STORE_ID_LAST DR_CUSTOMER PRIOR_1MO_ALCOHOLIC_BEVERAGES PRIOR_1MO_BAKERY PRIOR_1MO_BAKERY_PKD_OUTSIDE PRIOR_1MO_BAR PRIOR_1MO_CATERING PRIOR_1MO_DAIRY PRIOR_1MO_DELICATESSEN PRIOR_1MO_FLORAL PRIOR_1MO_FOOD_SERVICE PRIOR_1MO_FRONT_END_SERVICE PRIOR_1MO_FROZEN_GROCERY PRIOR_1MO_FUEL_STATION PRIOR_1MO_GM_HBC PRIOR_1MO_GROCERY PRIOR_1MO_JAMBA_JUICE PRIOR_1MO_MEAT PRIOR_1MO_PHARMACY PRIOR_1MO_PLATED_MEAL_KITS PRIOR_1MO_PRODUCE PRIOR_1MO_SEAFOOD PRIOR_1MO_STARBUCKS PRIOR_1MO_TOBACCO PRIOR_1MO_OWN_BRANDS_PERC PRIOR_1MO_FRESH_SALES_PERC PRIOR_3MO_ALCOHOLIC_BEVERAGES PRIOR_3MO_BAKERY PRIOR_3MO_BAKERY_PKD_OUTSIDE PRIOR_3MO_BAR PRIOR_3MO_CATERING PRIOR_3MO_DAIRY PRIOR_3MO_DELICATESSEN PRIOR_3MO_FLORAL PRIOR_3MO_FOOD_SERVICE PRIOR_3MO_FRONT_END_SERVICE PRIOR_3MO_FROZEN_GROCERY PRIOR_3MO_FUEL_STATION PRIOR_3MO_GM_HBC PRIOR_3MO_GROCERY PRIOR_3MO_JAMBA_JUICE PRIOR_3MO_MEAT PRIOR_3MO_PHARMACY PRIOR_3MO_PLATED_MEAL_KITS PRIOR_3MO_PRODUCE PRIOR_3MO_SEAFOOD PRIOR_3MO_STARBUCKS PRIOR_3MO_TOBACCO PRIOR_3MO_OWN_BRANDS_PERC PRIOR_3MO_FRESH_SALES_PERC INSTORE_TXN_DT NET_AMT MKDN_AMT TOTAL_ITEM_QTY CLIPPED_COUPONS LENGTH_OF_TIME_WD_ALB_DAYS MF_FACTS_SEGMENT_NAME MF_SHOP_STYLE_SEG_SEGMENT MF_TRUPRICE_SEGMENT MF_MY_NEEDS_SEGMENT IRI_SALES_SALES_DOLLAR_TY IRI_SALES_SALES_PER_CHANGE IRI_SALES_MARKET_SALES_PER_CHANGE IRI_SALES_SALES_PER_CHANGE_VS_MARKET_IN_PTS IRI_SALES_SALES_PER_SQ_FT LABOR_LABOR_DOLLAR_TY LABOR_LABOR_PER_TY LABOR_LABOR_PER_CHANGE_IN_PTS SHRINK_SHRINK_DOLLAR_TY SHRINK_SHRINK_PER_TY SHRINK_SHRINK_PER_CHANGE_IN_PTS COMPETITION_DOLLAR_AT_RISK FOOT_TRAFFIC_FOOT_TRAFFIC_PER_CHANGE NPS_NPS_YTD_FOR_ELITE_BEST NPS_NPS_LAST_4_WEEKS NPS_NPS_LAST_4_WEEKS_FOR_ELITE_BEST NPS_NPS_COUNT_YTD NPS_NPS_COUNT_YTD_FOR_ELITE_BEST NPS_NPS_COUNT_LAST_4_WEEKS NPS_NPS_COUNT_LAST_4_WEEKS_FOR_ELITE_BEST OFFERINGS_SERVICE_COUNTER_SALES_MIX_PER NEW_ITEMS_PER_NEW_PRODUCTS OWN_BRANDS_OWN_BRANDS_SALES_MIX_PER ECOMM_DUG_HH_MIX_PER ECOMM_HOME_DELIVERY_MIX_PER DEPT_MIX_PRODUCE_SALES_MIX_PER DEPT_MIX_MEALS_SALES_MIX_PER DEPT_MIX_HBC_SALES_MIX_PER DEPT_MIX_ETHNIC_PRODUCTS_MIX_PER DEPT_MIX_BABY_SALES_MIX_PER DEPT_MIX_PET_SALES_MIX_PER DEPT_MIX_FUEL_SALES_MIX_PER DEPT_MIX_STARBUCKS_SALES_MIX_PER SPACE_ALLOCATION_DAIRY SPACE_ALLOCATION_FROZEN_GROCERY SPACE_ALLOCATION_GM_HBC SPACE_ALLOCATION_GROCERY SPACE_ALLOCATION_OTHERS SPACE_ALLOCATION_PKGD_BAKERY AIV_AIV_TY AIV_AIV_PER_CHANGE MARKDOWN_MARKDOWN_PER HH_COUNTS_HH_COUNT_TY HH_COUNTS_HH_COUNT_PER_CHANGE OTHER_PER_HH_REDEEMING_J4U_OFFERS FACTS_ELITEBEST_PER_OF_SALES FACTS_GOOD_PER_OF_SALES FACTS_OCCASIONAL_PER_OF_SALES TRUPRICE_MOST_PRICE_DRIVEN_PER_OF_SALES TRUPRICE_PRICE_DRIVEN_PER_OF_SALES TRUPRICE_PRICE_NEUTRAL_PER_OF_SALES TRUPRICE_QUALITY_DRIVEN_PER_OF_SALES TRUPRICE_MOST_QUALITY_DRIVEN_PER_OF_SALES SHOPSTYLES_ORGANIC_LIVING_PER_OF_SALES SHOPSTYLES_COOKING_FROM_SCRATCH_PER_OF_SALES SHOPSTYLES_CONVENIENCE_SEEKERS_PER_OF_SALES SHOPSTYLES_HEALTHIER_ALTERNATIVES_PER_OF_SALES SHOPSTYLES_FAMILY_FOCUSED_PER_OF_SALES SHOPSTYLES_CONVENIENTLY_FRESH_PER_OF_SALES MYNEEDS_EASY_EATING_PER_OF_SALES MYNEEDS_ONE_STOP_LOW_PRICE_PER_OF_SALES MYNEEDS_HEALTHY_FOODIES_PER_OF_SALES MYNEEDS_CHASING_PRICE_PER_OF_SALES MYNEEDS_SCRATCH_FOODIES_PER_OF_SALES MYNEEDS_EASY_SHOPPING_PER_OF_SALES AGE_15_24_TRADE_AREA_PER AGE_15_24_VARIANCE_IN_PTS AGE_25_34_TRADE_AREA_PER AGE_25_34_VARIANCE_IN_PTS AGE_35_44_TRADE_AREA_PER AGE_35_44_VARIANCE_IN_PTS AGE_45_54_TRADE_AREA_PER AGE_45_54_VARIANCE_IN_PTS AGE_55_64_TRADE_AREA_PER AGE_55_64_VARIANCE_IN_PTS AGE_65_74_TRADE_AREA_PER AGE_65_74_VARIANCE_IN_PTS AGE_75_OR_MORE_TRADE_AREA_PER AGE_75_OR_MORE_VARIANCE_IN_PTS INCOM

In [0]:
# filtered_pd = spark.createDataFrame(pd_df_valid)
# filtered_pd.write.format("net.snowflake.spark.snowflake").options(**db_options).option("dbtable", "NK_FRACTAL_CUSTOMER_MASTER_TABLE_L3M_S4_EDA").mode('append').save()

# 5. Load Trained Model and get the predictions

In [0]:
df = spark.read.format("net.snowflake.spark.snowflake").options(**db_options).option("query", "Select * FROM EDM_BIZOPS_PRD.FBI.NK_FRACTAL_CUSTOMER_MASTER_TABLE_L3M_S4_EDA" ).load()


model_features = [
'HHS_ID',
'PRIOR_3_MONTH_STORE_AOV',
'CLIPPED_COUPONS',
'PRIOR_3MO_CLIPPED_COUPON',
'PRIOR_3_MONTH_MKDN_AMT',
'LENGTH_OF_TIME_WD_ALB_DAYS',
'DR_CUSTOMER',
'MF_MY_NEEDS_SEGMENT',
'MF_SHOP_STYLE_SEG_SEGMENT',
'MF_TRUPRICE_SEGMENT',
'PRIOR_3MO_PRODUCE',
'PRIOR_3MO_FLORAL',
'PRIOR_3MO_OWN_BRANDS_PERC',
'ECOMM_DUG_HH_MIX_PER',
'ECOMM_HOME_DELIVERY_MIX_PER',
'ETHNICITY_ASIAN_STORE_PER',
'IRI_SALES_SALES_DOLLAR_TY',
'OFFERINGS_SERVICE_COUNTER_SALES_MIX_PER',
'ECOM_AOV',
'MARKDOWN_MARKDOWN_PER',
'PHARMACY',
'COMPETITION_DOLLAR_AT_RISK',
'Age35plus_55_Medium_q',
'Income_150K_VeryHigh_q',
'Income_UND50K_Low_q',
'OWN_BRANDS_OWN_BRANDS_SALES_MIX_PER'
]

model_df = df.select(model_features)

In [0]:
model_pddf = model_df.toPandas()

# Shape of the dataset
print('Shape of the dataset: ', model_pddf.shape)

Shape of the dataset: (9079095, 26)

In [0]:
model_pddf['DR_CUSTOMER'] = model_pddf['DR_CUSTOMER'].astype(str) 


model_pddf.rename(columns={'PRIOR_3_MONTH_STORE_AOV':'PRIOR_3_MONTH_STORE_AOV',
                            'CLIPPED_COUPONS':'FRST_TXN_CLIPPED_COUPONS',
                            'PRIOR_3MO_CLIPPED_COUPON':'PRIOR_3_MONTHS_COUPONS_CLIPPED',
                            'PRIOR_3_MONTH_MKDN_AMT':'PRIOR_3_MONTH_MKDN_AMT',
                            'LENGTH_OF_TIME_WD_ALB_DAYS':'LENGTH_OF_TIME_WD_ALB_DAYS',
                            'DR_CUSTOMER':'DIGITALLY_REACHABLE_FLAG',
                            'MF_MY_NEEDS_SEGMENT':'FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN',
                            'MF_SHOP_STYLE_SEG_SEGMENT':'FRST_TXN_SHOP_STYLE_SEG_SEGMENT',
                            'MF_TRUPRICE_SEGMENT':'FRST_TXN_TRUPRICE_SEGMENT',
                            'PRIOR_3MO_PRODUCE':'PRIOR_3MO_PRODUCE',
                            'PRIOR_3MO_FLORAL':'PRIOR_3MO_FLORAL',
                            'PRIOR_3MO_OWN_BRANDS_PERC':'PRIOR_3MO_OWN_BRANDS_PERC',
                            'Age35plus_55_Medium_q':'Age35+_55_Medium_q'
                            },inplace=True)       

model_pddf['DIGITALLY_REACHABLE_FLAG'] = 'true'
model_pddf.loc[model_pddf['PHARMACY'] == True, 'PHARMACY'] = 'true'
model_pddf.loc[model_pddf['PHARMACY'] == False, 'PHARMACY'] = 'false'

model_pddf.head()

Out[18]:

HHS_ID 
 PRIOR_3_MONTH_STORE_AOV 
 FRST_TXN_CLIPPED_COUPONS 
 PRIOR_3_MONTHS_COUPONS_CLIPPED 
 PRIOR_3_MONTH_MKDN_AMT 
 LENGTH_OF_TIME_WD_ALB_DAYS 
 DIGITALLY_REACHABLE_FLAG 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT 
 FRST_TXN_TRUPRICE_SEGMENT 
 PRIOR_3MO_PRODUCE 
 PRIOR_3MO_FLORAL 
 PRIOR_3MO_OWN_BRANDS_PERC 
 ECOMM_DUG_HH_MIX_PER 
 ECOMM_HOME_DELIVERY_MIX_PER 
 ETHNICITY_ASIAN_STORE_PER 
 IRI_SALES_SALES_DOLLAR_TY 
 OFFERINGS_SERVICE_COUNTER_SALES_MIX_PER 
 ECOM_AOV 
 MARKDOWN_MARKDOWN_PER 
 PHARMACY 
 COMPETITION_DOLLAR_AT_RISK 
 Age35+_55_Medium_q 
 Income_150K_VeryHigh_q 
 Income_UND50K_Low_q 
 OWN_BRANDS_OWN_BRANDS_SALES_MIX_PER 
 
 
 
 
 0 
 990069279079 
 31.670000 
 5.0 
 4.0 
 -20.610000 
 1466.0 
 true 
 Chasing Price 
 CONVENIENCE SEEKERS 
 Most Price Driven 
 0.000000 
 0.000000 
 49.735760 
 0.024 
 0.008 
 0.05 
 6003778.0 
 0.022 
 89.04106 
 0.17 
 true 
 85996192.0 
 3 
 False 
 False 
 0.24 
 
 
 1 
 250041317078 
 30.606667 
 0.0 
 6.0 
 -6.390000 
 3811.0 
 true 
 One-Stop Low Price 
 FAMILY FOCUSED 
 Price Driven 
 16.302640 
 0.000000 
 28.705640 
 0.009 
 0.055 
 0.07 
 13828878.0 
 0.009 
 117.72486 
 0.16 
 false 
 146212448.0 
 False 
 3 
 False 
 0.26 
 
 
 2 
 990014933332 
 32.728000 
 8.0 
 22.0 
 -9.730000 
 2645.0 
 true 
 Healthy Foodies 
 COOKING FROM SCRATCH 
 UNCLASSIFIED 
 11.335259 
 6.180992 
 53.054380 
 0.031 
 0.014 
 0.03 
 7990885.0 
 0.017 
 78.46971 
 0.14 
 true 
 70091528.0 
 3 
 False 
 False 
 0.19 
 
 
 3 
 845036433620 
 25.320000 
 0.0 
 107.0 
 -28.510000 
 223.0 
 true 
 Chasing Price 
 FAMILY FOCUSED 
 Most Price Driven 
 0.000000 
 0.000000 
 17.083385 
 0.034 
 0.015 
 0.02 
 9161707.0 
 0.016 
 81.52408 
 0.18 
 true 
 71293712.0 
 3 
 False 
 3 
 0.24 
 
 
 4 
 990039409531 
 38.509410 
 0.0 
 6.0 
 -7.898824 
 1231.0 
 true 
 Easy Shopping 
 COOKING FROM SCRATCH 
 Price Neutral 
 5.801505 
 0.000000 
 23.861637 
 0.072 
 0.013 
 0.01 
 7819492.0 
 0.015 
 97.40615 
 0.18 
 true 
 49764936.0 
 False 
 False 
 3 
 0.21

In [0]:
model_data_backup = model_pddf.copy()

model_pddf.drop(columns = ['HHS_ID'],inplace=True)

In [0]:
bcols = model_pddf.select_dtypes('bool').columns.to_list()

f32cols = model_pddf.select_dtypes('float32').columns.to_list()
f64cols = model_pddf.select_dtypes('float64').columns.to_list()
intcols = model_pddf.select_dtypes('int32').columns.to_list()
ficols = f32cols + f64cols + intcols

string_columns = model_pddf.select_dtypes('object').columns.to_list()


categorical_cols = bcols + string_columns
numerical_cols = ficols
print("categorical_cols: ",len(categorical_cols))
print("numerical columns: ",len(numerical_cols))

categorical_cols: 8
numerical columns: 17

In [0]:
dummy_data = pd.get_dummies(
    model_pddf[categorical_cols],
    categorical_cols
)

dummy_data.head()

Out[26]:

DIGITALLY_REACHABLE_FLAG_true 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Chasing Price 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Eating 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Shopping 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Healthy Foodies 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_One-Stop Low Price 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Scratch Foodies 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENCE SEEKERS 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENTLY FRESH 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_COOKING FROM SCRATCH 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_FAMILY FOCUSED 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_HEALTHIER ALTERNATIVES 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_ORGANIC LIVING 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_UNCLASSIFIED 
 FRST_TXN_TRUPRICE_SEGMENT_Most Price Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Most Quality Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Price Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Price Neutral 
 FRST_TXN_TRUPRICE_SEGMENT_Quality Driven 
 FRST_TXN_TRUPRICE_SEGMENT_UNCLASSIFIED 
 PHARMACY_false 
 PHARMACY_true 
 Age35+_55_Medium_q_3 
 Age35+_55_Medium_q_False 
 Income_150K_VeryHigh_q_3 
 Income_150K_VeryHigh_q_False 
 Income_UND50K_Low_q_3 
 Income_UND50K_Low_q_False 
 
 
 
 
 0 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 0 
 0 
 1 
 0 
 1 
 
 
 1 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 1 
 0 
 0 
 1 
 1 
 0 
 0 
 1 
 
 
 2 
 1 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 1 
 1 
 0 
 0 
 1 
 0 
 1 
 
 
 3 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 0 
 0 
 1 
 1 
 0 
 
 
 4 
 1 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 1 
 0 
 1 
 0 
 1 
 1 
 0

In [0]:
# Drop columns with FALSE suffix
dummy_data = dummy_data.drop(dummy_data.filter(regex='_false').columns, axis=1)
dummy_data = dummy_data.drop(dummy_data.filter(regex='_False').columns, axis=1)
dummy_data.head()

Out[27]:

DIGITALLY_REACHABLE_FLAG_true 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Chasing Price 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Eating 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Shopping 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Healthy Foodies 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_One-Stop Low Price 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Scratch Foodies 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENCE SEEKERS 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENTLY FRESH 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_COOKING FROM SCRATCH 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_FAMILY FOCUSED 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_HEALTHIER ALTERNATIVES 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_ORGANIC LIVING 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_UNCLASSIFIED 
 FRST_TXN_TRUPRICE_SEGMENT_Most Price Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Most Quality Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Price Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Price Neutral 
 FRST_TXN_TRUPRICE_SEGMENT_Quality Driven 
 FRST_TXN_TRUPRICE_SEGMENT_UNCLASSIFIED 
 PHARMACY_true 
 Age35+_55_Medium_q_3 
 Income_150K_VeryHigh_q_3 
 Income_UND50K_Low_q_3 
 
 
 
 
 0 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 0 
 0 
 
 
 1 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 
 
 2 
 1 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 
 
 3 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 0 
 1 
 
 
 4 
 1 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 1 
 0 
 0 
 1

In [0]:
pd_df_copy = model_pddf.copy()

pd_df_copy = pd_df_copy.drop(categorical_cols, axis=1)

dummy_data = pd.concat([pd_df_copy,dummy_data], axis=1)

dummy_data.head()

Out[28]:

PRIOR_3_MONTH_STORE_AOV 
 FRST_TXN_CLIPPED_COUPONS 
 PRIOR_3_MONTHS_COUPONS_CLIPPED 
 PRIOR_3_MONTH_MKDN_AMT 
 LENGTH_OF_TIME_WD_ALB_DAYS 
 PRIOR_3MO_PRODUCE 
 PRIOR_3MO_FLORAL 
 PRIOR_3MO_OWN_BRANDS_PERC 
 ECOMM_DUG_HH_MIX_PER 
 ECOMM_HOME_DELIVERY_MIX_PER 
 ETHNICITY_ASIAN_STORE_PER 
 IRI_SALES_SALES_DOLLAR_TY 
 OFFERINGS_SERVICE_COUNTER_SALES_MIX_PER 
 ECOM_AOV 
 MARKDOWN_MARKDOWN_PER 
 COMPETITION_DOLLAR_AT_RISK 
 OWN_BRANDS_OWN_BRANDS_SALES_MIX_PER 
 DIGITALLY_REACHABLE_FLAG_true 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Chasing Price 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Eating 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Shopping 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Healthy Foodies 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_One-Stop Low Price 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Scratch Foodies 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENCE SEEKERS 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENTLY FRESH 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_COOKING FROM SCRATCH 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_FAMILY FOCUSED 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_HEALTHIER ALTERNATIVES 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_ORGANIC LIVING 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_UNCLASSIFIED 
 FRST_TXN_TRUPRICE_SEGMENT_Most Price Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Most Quality Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Price Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Price Neutral 
 FRST_TXN_TRUPRICE_SEGMENT_Quality Driven 
 FRST_TXN_TRUPRICE_SEGMENT_UNCLASSIFIED 
 PHARMACY_true 
 Age35+_55_Medium_q_3 
 Income_150K_VeryHigh_q_3 
 Income_UND50K_Low_q_3 
 
 
 
 
 0 
 31.670000 
 5.0 
 4.0 
 -20.610000 
 1466.0 
 0.000000 
 0.000000 
 49.735760 
 0.024 
 0.008 
 0.05 
 6003778.0 
 0.022 
 89.04106 
 0.17 
 85996192.0 
 0.24 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 0 
 0 
 
 
 1 
 30.606667 
 0.0 
 6.0 
 -6.390000 
 3811.0 
 16.302640 
 0.000000 
 28.705640 
 0.009 
 0.055 
 0.07 
 13828878.0 
 0.009 
 117.72486 
 0.16 
 146212448.0 
 0.26 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 
 
 2 
 32.728000 
 8.0 
 22.0 
 -9.730000 
 2645.0 
 11.335259 
 6.180992 
 53.054380 
 0.031 
 0.014 
 0.03 
 7990885.0 
 0.017 
 78.46971 
 0.14 
 70091528.0 
 0.19 
 1 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 1 
 0 
 0 
 
 
 3 
 25.320000 
 0.0 
 107.0 
 -28.510000 
 223.0 
 0.000000 
 0.000000 
 17.083385 
 0.034 
 0.015 
 0.02 
 9161707.0 
 0.016 
 81.52408 
 0.18 
 71293712.0 
 0.24 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 1 
 0 
 1 
 
 
 4 
 38.509410 
 0.0 
 6.0 
 -7.898824 
 1231.0 
 5.801505 
 0.000000 
 23.861637 
 0.072 
 0.013 
 0.01 
 7819492.0 
 0.015 
 97.40615 
 0.18 
 49764936.0 
 0.21 
 1 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 1 
 0 
 0 
 1

In [0]:
dummy_data.drop(columns=['FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Scratch Foodies','FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Eating','FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Easy Shopping','FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Healthy Foodies',      
                         'FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_Chasing Price',
                         'FRST_TXN_SHOP_STYLE_SEG_SEGMENT_UNCLASSIFIED', 'FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENTLY FRESH','FRST_TXN_SHOP_STYLE_SEG_SEGMENT_FAMILY FOCUSED','FRST_TXN_SHOP_STYLE_SEG_SEGMENT_HEALTHIER ALTERNATIVES',
                         'FRST_TXN_SHOP_STYLE_SEG_SEGMENT_ORGANIC LIVING',
                         'FRST_TXN_TRUPRICE_SEGMENT_UNCLASSIFIED','FRST_TXN_TRUPRICE_SEGMENT_Quality Driven','FRST_TXN_TRUPRICE_SEGMENT_Price Driven','FRST_TXN_TRUPRICE_SEGMENT_Price Neutral'],inplace=True)
dummy_data.head()

Out[29]:

PRIOR_3_MONTH_STORE_AOV 
 FRST_TXN_CLIPPED_COUPONS 
 PRIOR_3_MONTHS_COUPONS_CLIPPED 
 PRIOR_3_MONTH_MKDN_AMT 
 LENGTH_OF_TIME_WD_ALB_DAYS 
 PRIOR_3MO_PRODUCE 
 PRIOR_3MO_FLORAL 
 PRIOR_3MO_OWN_BRANDS_PERC 
 ECOMM_DUG_HH_MIX_PER 
 ECOMM_HOME_DELIVERY_MIX_PER 
 ETHNICITY_ASIAN_STORE_PER 
 IRI_SALES_SALES_DOLLAR_TY 
 OFFERINGS_SERVICE_COUNTER_SALES_MIX_PER 
 ECOM_AOV 
 MARKDOWN_MARKDOWN_PER 
 COMPETITION_DOLLAR_AT_RISK 
 OWN_BRANDS_OWN_BRANDS_SALES_MIX_PER 
 DIGITALLY_REACHABLE_FLAG_true 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN_One-Stop Low Price 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_CONVENIENCE SEEKERS 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT_COOKING FROM SCRATCH 
 FRST_TXN_TRUPRICE_SEGMENT_Most Price Driven 
 FRST_TXN_TRUPRICE_SEGMENT_Most Quality Driven 
 PHARMACY_true 
 Age35+_55_Medium_q_3 
 Income_150K_VeryHigh_q_3 
 Income_UND50K_Low_q_3 
 
 
 
 
 0 
 31.670000 
 5.0 
 4.0 
 -20.610000 
 1466.0 
 0.000000 
 0.000000 
 49.735760 
 0.024 
 0.008 
 0.05 
 6003778.0 
 0.022 
 89.04106 
 0.17 
 85996192.0 
 0.24 
 1 
 0 
 1 
 0 
 1 
 0 
 1 
 1 
 0 
 0 
 
 
 1 
 30.606667 
 0.0 
 6.0 
 -6.390000 
 3811.0 
 16.302640 
 0.000000 
 28.705640 
 0.009 
 0.055 
 0.07 
 13828878.0 
 0.009 
 117.72486 
 0.16 
 146212448.0 
 0.26 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 
 
 2 
 32.728000 
 8.0 
 22.0 
 -9.730000 
 2645.0 
 11.335259 
 6.180992 
 53.054380 
 0.031 
 0.014 
 0.03 
 7990885.0 
 0.017 
 78.46971 
 0.14 
 70091528.0 
 0.19 
 1 
 0 
 0 
 1 
 0 
 0 
 1 
 1 
 0 
 0 
 
 
 3 
 25.320000 
 0.0 
 107.0 
 -28.510000 
 223.0 
 0.000000 
 0.000000 
 17.083385 
 0.034 
 0.015 
 0.02 
 9161707.0 
 0.016 
 81.52408 
 0.18 
 71293712.0 
 0.24 
 1 
 0 
 0 
 0 
 1 
 0 
 1 
 1 
 0 
 1 
 
 
 4 
 38.509410 
 0.0 
 6.0 
 -7.898824 
 1231.0 
 5.801505 
 0.000000 
 23.861637 
 0.072 
 0.013 
 0.01 
 7819492.0 
 0.015 
 97.40615 
 0.18 
 49764936.0 
 0.21 
 1 
 0 
 0 
 1 
 0 
 0 
 1 
 0 
 0 
 1

In [0]:
from joblib import Parallel, delayed
import joblib

# Load the model from the file
XG_from_pickle = joblib.load('/dbfs/FileStore/Models/BNC_to_eCom.pkl')

In [0]:
# Use the loaded model to make predictions
pred = XG_from_pickle.predict(dummy_data)
pred = pd.DataFrame(pred)
pred

Out[34]:

0 
 
 
 
 
 0 
 1 
 
 
 1 
 1 
 
 
 2 
 1 
 
 
 3 
 1 
 
 
 4 
 1 
 
 
 ... 
 ... 
 
 
 9079090 
 1 
 
 
 9079091 
 1 
 
 
 9079092 
 1 
 
 
 9079093 
 1 
 
 
 9079094 
 1 
 
 
 
 9079095 rows × 1 columns

In [0]:
prob_pred = XG_from_pickle.predict_proba(dummy_data)
prob_pred = pd.DataFrame(prob_pred).reset_index()
prob_pred

Out[36]:

index 
 0 
 1 
 
 
 
 
 0 
 0 
 0.387060 
 0.612940 
 
 
 1 
 1 
 0.397121 
 0.602879 
 
 
 2 
 2 
 0.396227 
 0.603773 
 
 
 3 
 3 
 0.462851 
 0.537149 
 
 
 4 
 4 
 0.418374 
 0.581626 
 
 
 ... 
 ... 
 ... 
 ... 
 
 
 9079090 
 9079090 
 0.270506 
 0.729494 
 
 
 9079091 
 9079091 
 0.267229 
 0.732771 
 
 
 9079092 
 9079092 
 0.291243 
 0.708757 
 
 
 9079093 
 9079093 
 0.271661 
 0.728339 
 
 
 9079094 
 9079094 
 0.396833 
 0.603167 
 
 
 
 9079095 rows × 3 columns

In [0]:
model_data_backup['0'] = prob_pred[0]
model_data_backup['1'] = prob_pred[1]

model_data_backup.head()

Out[41]:

HHS_ID 
 PRIOR_3_MONTH_STORE_AOV 
 FRST_TXN_CLIPPED_COUPONS 
 PRIOR_3_MONTHS_COUPONS_CLIPPED 
 PRIOR_3_MONTH_MKDN_AMT 
 LENGTH_OF_TIME_WD_ALB_DAYS 
 DIGITALLY_REACHABLE_FLAG 
 FRST_TXN_MY_NEEDS_FIRST_ECOMM_TXN 
 FRST_TXN_SHOP_STYLE_SEG_SEGMENT 
 FRST_TXN_TRUPRICE_SEGMENT 
 PRIOR_3MO_PRODUCE 
 PRIOR_3MO_FLORAL 
 PRIOR_3MO_OWN_BRANDS_PERC 
 ECOMM_DUG_HH_MIX_PER 
 ECOMM_HOME_DELIVERY_MIX_PER 
 ETHNICITY_ASIAN_STORE_PER 
 IRI_SALES_SALES_DOLLAR_TY 
 OFFERINGS_SERVICE_COUNTER_SALES_MIX_PER 
 ECOM_AOV 
 MARKDOWN_MARKDOWN_PER 
 PHARMACY 
 COMPETITION_DOLLAR_AT_RISK 
 Age35+_55_Medium_q 
 Income_150K_VeryHigh_q 
 Income_UND50K_Low_q 
 OWN_BRANDS_OWN_BRANDS_SALES_MIX_PER 
 0 
 1 
 
 
 
 
 0 
 990069279079 
 31.670000 
 5.0 
 4.0 
 -20.610000 
 1466.0 
 true 
 Chasing Price 
 CONVENIENCE SEEKERS 
 Most Price Driven 
 0.000000 
 0.000000 
 49.735760 
 0.024 
 0.008 
 0.05 
 6003778.0 
 0.022 
 89.04106 
 0.17 
 true 
 85996192.0 
 3 
 False 
 False 
 0.24 
 0.387060 
 0.612940 
 
 
 1 
 250041317078 
 30.606667 
 0.0 
 6.0 
 -6.390000 
 3811.0 
 true 
 One-Stop Low Price 
 FAMILY FOCUSED 
 Price Driven 
 16.302640 
 0.000000 
 28.705640 
 0.009 
 0.055 
 0.07 
 13828878.0 
 0.009 
 117.72486 
 0.16 
 false 
 146212448.0 
 False 
 3 
 False 
 0.26 
 0.397121 
 0.602879 
 
 
 2 
 990014933332 
 32.728000 
 8.0 
 22.0 
 -9.730000 
 2645.0 
 true 
 Healthy Foodies 
 COOKING FROM SCRATCH 
 UNCLASSIFIED 
 11.335259 
 6.180992 
 53.054380 
 0.031 
 0.014 
 0.03 
 7990885.0 
 0.017 
 78.46971 
 0.14 
 true 
 70091528.0 
 3 
 False 
 False 
 0.19 
 0.396227 
 0.603773 
 
 
 3 
 845036433620 
 25.320000 
 0.0 
 107.0 
 -28.510000 
 223.0 
 true 
 Chasing Price 
 FAMILY FOCUSED 
 Most Price Driven 
 0.000000 
 0.000000 
 17.083385 
 0.034 
 0.015 
 0.02 
 9161707.0 
 0.016 
 81.52408 
 0.18 
 true 
 71293712.0 
 3 
 False 
 3 
 0.24 
 0.462851 
 0.537149 
 
 
 4 
 990039409531 
 38.509410 
 0.0 
 6.0 
 -7.898824 
 1231.0 
 true 
 Easy Shopping 
 COOKING FROM SCRATCH 
 Price Neutral 
 5.801505 
 0.000000 
 23.861637 
 0.072 
 0.013 
 0.01 
 7819492.0 
 0.015 
 97.40615 
 0.18 
 true 
 49764936.0 
 False 
 False 
 3 
 0.21 
 0.418374 
 0.581626

In [0]:
filtered_pd = spark.createDataFrame(model_data_backup)
filtered_pd.write.format("net.snowflake.spark.snowflake").options(**db_options).option("dbtable", "NK_FRACTAL_CUSTOMER_MASTER_TABLE_L3M_S4_EDA_WP").mode('append').save()

# 5. Bivariate Analysis

## 5.0  Generation of pd_df_valid_bivariate DF

In [0]:
# Read customer data (NK_FRACTAL_BNCS_CUSTOMER_MASTER) - Since we are only targeting the BNC to eom,BNC to ACI and Reactivated for this analysis
df = spark.read.format("net.snowflake.spark.snowflake").options(**db_options).option("query", "Select * FROM EDM_BIZOPS_PRD.FBI.NK_FRACTAL_BNC_TO_ECOM_EDA" ).load()
pd_df_valid_bivariate = df.toPandas()
# Shape of the dataset
print('Shape of the dataset: ', pd_df_valid_bivariate.shape)

In [0]:
print(pd_df_valid_bivariate.shape)

bcols = pd_df_valid_bivariate.select_dtypes('bool').columns.to_list()
print('Boolean columns: ',len(bcols))

dtcols = pd_df_valid_bivariate.select_dtypes('datetime').columns.to_list()
print('Datetime columns: ',len(dtcols))

f32cols = pd_df_valid_bivariate.select_dtypes('float32').columns.to_list()
f64cols = pd_df_valid_bivariate.select_dtypes('float64').columns.to_list()
intcols = pd_df_valid_bivariate.select_dtypes('int32').columns.to_list()
ficols = f32cols + f64cols + intcols
print('Float columns: ',len(ficols))

string_columns = pd_df_valid_bivariate.select_dtypes('object').columns.to_list()
print('String columns: ',len(string_columns))


categorical_cols = bcols + string_columns
numerical_cols = ficols

In [0]:
display(pd_df_valid_bivariate[ficols].head())

## 5.1. Churn vs independent vars

### a. Categorical Description

In [0]:
str_cols = string_columns
bool_cols = bcols
target_cols = ['BNC_FLAG', 'ECOM_CHURN_FLAG', 'OMNI_CHURN_FLAG','CUS_SEGMENT','LU_BANNER','LU_DIVISION','HOUSEHOLD_ID']
categorical_cols = string_columns + bcols
for x in target_cols:
  if x in categorical_cols:
    categorical_cols.remove(x)

# We have only 3 features which are specific to delivery type - one is dug status other two is delivery status and carrier type
dug_cat = ['FRST_TXN_DUG_STATUS']
dlvy_cat = ['FRST_TXN_DELIVERY_STATUS',
              'FRST_TXN_CARRIER_TYPE']

rest_metrics = []

for x in categorical_cols:
  if x not in dlvy_cat and x not in dug_cat:
    rest_metrics.append(x)

print(len(rest_metrics))

In [0]:
# pd_df_valid_bivariate = pd_df_valid_bivariate.replace(True,"True")
# pd_df_valid_bivariate = pd_df_valid_bivariate.replace(False,"False")

pd_df_valid_bivariate_dug = pd_df_valid_bivariate[pd_df_valid_bivariate['FRST_TXN_DELIVERY_TYPE'] == 'DUG']  # DUG specific
pd_df_valid_bivariate_dlvry = pd_df_valid_bivariate[pd_df_valid_bivariate['FRST_TXN_DELIVERY_TYPE'] == 'DELIVERY']  # Delivery specific
print(len(pd_df_valid_bivariate_dug))
print(len(pd_df_valid_bivariate_dlvry))

categorical_desc = pd.DataFrame()
categorical_desc_overall = pd.DataFrame()
categorical_desc_level2 = pd.DataFrame()

filters = ['LU_BANNER','LU_DIVISION']
segments = ['Overall','LU_BANNER','LU_DIVISION']
columns_order = ['Feature_Name','Filter_Metric','Filter_Values','Feature_Values','CUS_SEGMENT','Overall_Category_Count','ECOM_CHURN_FLAG','Ecom_Flag_Count','ECOM_CHURN_PER']
z = 0
for each_seg in segments:
  print(each_seg)
  if z == 0:
    categorical_count1 = aggregate_overall(pd_df_valid_bivariate, rest_metrics,each_seg)
    categorical_desc_overall = categorical_desc_overall.append(categorical_count1)
    
    categorical_count2 = aggregate_overall(pd_df_valid_bivariate_dug, dug_cat,each_seg)
    categorical_desc_overall = categorical_desc_overall.append(categorical_count2)
    
    categorical_count3 = aggregate_overall(pd_df_valid_bivariate_dlvry, dlvy_cat,each_seg)
    categorical_desc_overall = categorical_desc_overall.append(categorical_count3)
    
    categorical_desc_overall['CUS_SEGMENT'] = 'BNC TO ECOM'

categorical_desc_overall = categorical_desc_overall[columns_order]

In [0]:
display(categorical_desc_overall)

### b. Numerical

In [0]:
#numerical_cols
#pd_df_valid_bivariate
print(len(numerical_cols))
print(len(ficols))

In [0]:
#Create list for categorical and numerical features
dug_n = ['FRST_TXN_WAIT_TIME_IN_MINS']

delivery_n = ['FRST_TXN_DELIVERY_DELAY',
              'FRST_TXN_DRIVE_DISTANCE',
              'FRST_TXN_DRIVE_TIME']

stnc_n = ['STORE_SUM_SALES_1MO',
          'STORE_AOV_1MO',
          'STORE_TXNS_1MO',
          'STORE_AVG_MKDN_AMT_1MO',
          'STORE_SUM_SALES_3MO',
          'STORE_AOV_3MO',
          'STORE_TXNS_3MO',
          'STORE_AVG_MKDN_AMT_3MO']
ecomnc_n = ['ECOMM_SUM_SALES_1MO',
            'ECOMM_AOV_1MO',
            'ECOMM_TXNS_1MO',
            'ECOMM_AVG_MKDN_AMT_1MO',
            'ECOMM_SUM_SALES_3MO',
            'ECOMM_AOV_3MO',
            'ECOMM_TXNS_3MO',
            'ECOMM_AVG_MKDN_AMT_3MO',
            'COUPONS_CLIPPED_1MO',
            'COUPONS_CLIPPED_3MO']

aciex_n = ['PRIOR_3_MONTH_STORE_TXNS',
          'PRIOR_3_MONTH_TOTAL_NET_SALES',
          'PRIOR_3_MONTH_STORE_AOV',
          'PRIOR_3_MONTH_MKDN_AMT',
          'PRIOR_3_MONTHS_COUPONS_CLIPPED',
          'PRIOR_1_MONTH_STORE_TXNS',
          'PRIOR_1_MONTH_TOTAL_NET_SALES',
          'PRIOR_1_MONTH_STORE_AOV',
          'PRIOR_1_MONTH_MKDN_AMT',
          'PRIOR_1_MONTHS_COUPONS_CLIPPED',
          'PRIOR_RATIO_STORE_TXNS',
          'PRIOR_RATIO_NET_SALES',
          'PRIOR_RATIO_AOV',
          'PRIOR_RATIO_AVG_MKDN_AMT',
          'PRIOR_RATIO_COUPONS_CLIPPED',
          'PRIOR_1MO_ALCOHOLIC_BEVERAGES',
          'PRIOR_1MO_BAKERY',
          'PRIOR_1MO_BAKERY_PKD_OUTSIDE',
          'PRIOR_1MO_DAIRY',
          'PRIOR_1MO_DELICATESSEN',
          'PRIOR_1MO_FLORAL',
          'PRIOR_1MO_FOOD_SERVICE',
          'PRIOR_1MO_FRONT_END_SERVICE',
          'PRIOR_1MO_FROZEN_GROCERY',
          'PRIOR_1MO_FUEL_STATION',
          'PRIOR_1MO_GM_HBC',
          'PRIOR_1MO_GROCERY',
          'PRIOR_1MO_MEAT',
          'PRIOR_1MO_PHARMACY',
          'PRIOR_1MO_PRODUCE',
          'PRIOR_1MO_SEAFOOD',
          'PRIOR_1MO_STARBUCKS',
          'PRIOR_1MO_TOBACCO',
          'PRIOR_1MO_OWN_BRANDS_PERC',
          'PRIOR_1MO_FRESH_SALES_PERC',
          'PRIOR_3MO_ALCOHOLIC_BEVERAGES',
          'PRIOR_3MO_BAKERY',
          'PRIOR_3MO_BAKERY_PKD_OUTSIDE',
          'PRIOR_3MO_DAIRY',
          'PRIOR_3MO_DELICATESSEN',
          'PRIOR_3MO_FLORAL',
          'PRIOR_3MO_FOOD_SERVICE',
          'PRIOR_3MO_FRONT_END_SERVICE',
          'PRIOR_3MO_FROZEN_GROCERY',
          'PRIOR_3MO_FUEL_STATION',
          'PRIOR_3MO_GM_HBC',
          'PRIOR_3MO_GROCERY',
          'PRIOR_3MO_MEAT',
          'PRIOR_3MO_PHARMACY',
          'PRIOR_3MO_PRODUCE',
          'PRIOR_3MO_SEAFOOD',
          'PRIOR_3MO_STARBUCKS',
          'PRIOR_3MO_TOBACCO',
          'PRIOR_3MO_OWN_BRANDS_PERC',
          'PRIOR_3MO_FRESH_SALES_PERC']

all_nspecific_cols = dug_n+delivery_n+stnc_n+ecomnc_n+aciex_n
numerical_cols_filtered = []

for x in ficols:
  if x not in all_nspecific_cols:
    numerical_cols_filtered.append(x)

print('Total Columns ',len(ficols))
print(len(numerical_cols_filtered))
print(len(all_nspecific_cols))

pd_df_valid_bivariate_dug = pd_df_valid_bivariate[pd_df_valid_bivariate['FRST_TXN_DELIVERY_TYPE'] == 'DUG']  # DUG specific
pd_df_valid_bivariate_dlvry = pd_df_valid_bivariate[pd_df_valid_bivariate['FRST_TXN_DELIVERY_TYPE'] == 'DELIVERY']  # Delivery specific
pd_df_valid_bivariate_ecomnc = pd_df_valid_bivariate[pd_df_valid_bivariate['ECOM_CHURN_FLAG'] == 'false']  # Ecom Non Churned specific
pd_df_valid_bivariate_storenc = pd_df_valid_bivariate[pd_df_valid_bivariate['OMNI_CHURN_FLAG'] == 'false']  # Omnichannel non churned specific
pd_df_valid_bivariate_ex_aci = pd_df_valid_bivariate[pd_df_valid_bivariate['CUS_SEGMENT'] != 'BNC to ACI']  # BNC to ACI excl. specific

print('DUG Data rows :',len(pd_df_valid_bivariate_dug))
print('Delivery Data rows :',len(pd_df_valid_bivariate_dlvry))
print('Ecom Non Churned Data rows :',len(pd_df_valid_bivariate_ecomnc))
print('Store Non Churned Data rows :',len(pd_df_valid_bivariate_storenc))
print('ACI Exclusing Data rows :',len(pd_df_valid_bivariate_ex_aci))

In [0]:
#First get Decile columns for all numerical vars according to specific universe
def get_decile_mark_v4(data, metrics, result):
  for i in metrics:
    data[i] = data[i].astype(float)
    subset2 = data[(data[i]==0)] 
    subset3 = data[(data[i]!=0)]

    if len(subset3)>1:
      q1 = np.percentile(subset3[i], 25)
      q2 = np.percentile(subset3[i], 50)
      q3 = np.percentile(subset3[i], 75)
      q4 = np.percentile(subset3[i], 100)
      
      q1_data = subset3.loc[(subset3[i] <= q1)]
      q2_data = subset3.loc[(subset3[i] > q1)&(subset3[i] <= q2)]
      q3_data = subset3.loc[(subset3[i] > q2)&(subset3[i] <= q3)]
      q4_data = subset3.loc[(subset3[i] > q3)&(subset3[i] <= q4)]

      q0_per = 0
      if len(subset2)>0:
        q0_per = len(subset2[subset2['ECOM_CHURN_FLAG'] == 'true'])/len(subset2)
      q1_per = 0
      if len(q1_data)>0:
        q1_per = len(q1_data[q1_data['ECOM_CHURN_FLAG'] == 'true'])/len(q1_data)
      q2_per = 0
      if len(q2_data)>0:
        q2_per = len(q2_data[q2_data['ECOM_CHURN_FLAG'] == 'true'])/len(q2_data)
      q3_per = 0
      if len(q3_data)>0:
        q3_per = len(q3_data[q3_data['ECOM_CHURN_FLAG'] == 'true'])/len(q3_data)
      q4_per = 0
      if len(q4_data)>0:
        q4_per = len(q4_data[q4_data['ECOM_CHURN_FLAG'] == 'true'])/len(q4_data)

      result.loc[len(result)] = [i,'00',0,len(subset2),len(subset2[subset2['ECOM_CHURN_FLAG'] == 'true']),q0_per]
      result.loc[len(result)] = [i,'01',q1,len(q1_data),len(q1_data[q1_data['ECOM_CHURN_FLAG'] == 'true']),q1_per]
      result.loc[len(result)] = [i,'02',q2,len(q2_data),len(q2_data[q2_data['ECOM_CHURN_FLAG'] == 'true']),q2_per]
      result.loc[len(result)] = [i,'03',q3,len(q3_data),len(q3_data[q3_data['ECOM_CHURN_FLAG'] == 'true']),q3_per]
      result.loc[len(result)] = [i,'04',q4,len(q4_data),len(q4_data[q4_data['ECOM_CHURN_FLAG'] == 'true']),q4_per]

  return result

In [0]:
result = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])

In [0]:
print('Dug')
result = get_decile_mark_v4(pd_df_valid_bivariate_dug,dug_n,result)
print('Delivery')
result = get_decile_mark_v4(pd_df_valid_bivariate_dlvry,delivery_n,result)
print('eCom NC')
result = get_decile_mark_v4(pd_df_valid_bivariate_ecomnc,ecomnc_n,result)
print('Store NC')
result = get_decile_mark_v4(pd_df_valid_bivariate_storenc,stnc_n,result)
print('Excl ACI')
result = get_decile_mark_v4(pd_df_valid_bivariate_ex_aci,aciex_n,result)
print('Overall')
result = get_decile_mark_v4(pd_df_valid_bivariate,numerical_cols_filtered,result)

In [0]:
display(result)

In [0]:
banner_result = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage','Level','Level_Value'])

In [0]:
banner_list = pd_df_valid_bivariate['LU_BANNER'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_dug[pd_df_valid_bivariate_dug['LU_BANNER'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,dug_n,br)
  br['Level'] = 'Banner'
  br['Level_Value'] = each_banner

  banner_result = banner_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_BANNER'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_dlvry[pd_df_valid_bivariate_dlvry['LU_BANNER'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,delivery_n,br)
  br['Level'] = 'Banner'
  br['Level_Value'] = each_banner

  banner_result = banner_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_BANNER'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_ecomnc[pd_df_valid_bivariate_ecomnc['LU_BANNER'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,ecomnc_n,br)
  br['Level'] = 'Banner'
  br['Level_Value'] = each_banner

  banner_result = banner_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_BANNER'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_storenc[pd_df_valid_bivariate_storenc['LU_BANNER'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,stnc_n,br)
  br['Level'] = 'Banner'
  br['Level_Value'] = each_banner

  banner_result = banner_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_BANNER'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_ex_aci[pd_df_valid_bivariate_ex_aci['LU_BANNER'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,aciex_n,br)
  br['Level'] = 'Banner'
  br['Level_Value'] = each_banner

  banner_result = banner_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_BANNER'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate[pd_df_valid_bivariate['LU_BANNER'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,numerical_cols_filtered,br)
  br['Level'] = 'Banner'
  br['Level_Value'] = each_banner

  banner_result = banner_result.append(br)

In [0]:
display(banner_result)

In [0]:
division_result = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage','Level','Level_Value'])

In [0]:
banner_list = pd_df_valid_bivariate['LU_DIVISION'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_dug[pd_df_valid_bivariate_dug['LU_DIVISION'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,dug_n,br)
  br['Level'] = 'Division'
  br['Level_Value'] = each_banner

  division_result = division_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_DIVISION'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_dlvry[pd_df_valid_bivariate_dlvry['LU_DIVISION'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,delivery_n,br)
  br['Level'] = 'Division'
  br['Level_Value'] = each_banner

  division_result = division_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_DIVISION'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_ecomnc[pd_df_valid_bivariate_ecomnc['LU_DIVISION'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,ecomnc_n,br)
  br['Level'] = 'Division'
  br['Level_Value'] = each_banner

  division_result = division_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_DIVISION'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_storenc[pd_df_valid_bivariate_storenc['LU_DIVISION'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,stnc_n,br)
  br['Level'] = 'Division'
  br['Level_Value'] = each_banner

  division_result = division_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_DIVISION'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate_ex_aci[pd_df_valid_bivariate_ex_aci['LU_DIVISION'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,aciex_n,br)
  br['Level'] = 'Division'
  br['Level_Value'] = each_banner

  division_result = division_result.append(br)

In [0]:
banner_list = pd_df_valid_bivariate['LU_DIVISION'].unique()
for each_banner in banner_list:
  banner_data = pd_df_valid_bivariate[pd_df_valid_bivariate['LU_DIVISION'] == each_banner]
  br = pd.DataFrame(columns=['Feature_Name','Quartile','Threshold','Total_Count','Churn_Count','Churn_Percentage'])
  br = get_decile_mark_v4(banner_data,numerical_cols_filtered,br)
  br['Level'] = 'Division'
  br['Level_Value'] = each_banner

  division_result = division_result.append(br)

In [0]:
display(division_result)